# Exploratory Data Analysis and Feature Engineering
### Section 0 - Environment Set-up

In [0]:
from pyspark.sql.functions import col, substring, split, when, lit, max as pyspark_max, min as pyspark_min, countDistinct, count, mean, sum as pyspark_sum, expr, to_utc_timestamp, to_timestamp, concat, length, unix_timestamp
from pyspark.sql import SQLContext
from pyspark.sql.types import IntegerType, StringType, BooleanType, DateType, DoubleType
import pandas as pd
from gcmap import GCMapper, Gradient
import matplotlib.pyplot as plt
from pandas.tseries.holiday import USFederalHolidayCalendar

blob_container = "w261team07container" # The name of your container created in https://portal.azure.com
storage_account = "w261team07storage" # The name of your Storage account created in https://portal.azure.com
secret_scope = "w261team07" # The name of the scope created in your local computer using the Databricks CLI
secret_key = "w261team07-key" # The name of the secret key created in your local computer using the Databricks CLI 
blob_url = f"wasbs://{blob_container}@{storage_account}.blob.core.windows.net"
mount_path = "/mnt/mids-w261"

spark.conf.set(
  f"fs.azure.sas.{blob_container}.{storage_account}.blob.core.windows.net",
  dbutils.secrets.get(scope = secret_scope, key = secret_key)
)

### Section 1 - Cleaning individual tables

We'll do our cleaning and preparation with a 3 month subset dataset in order to test the functions before applying to a larger dataset. We start by loading and examining the subset:

In [0]:
# Load the full airline dataset
df_airlines_full = spark.read.parquet("/mnt/mids-w261/datasets_final_project/parquet_airlines_data/*")

# Load the full weather dataset
df_weather_full = spark.read.parquet("/mnt/mids-w261/datasets_final_project/weather_data/*")

# Load the weather stations data
df_stations = spark.read.parquet("/mnt/mids-w261/datasets_final_project/stations_data/*")

# Load 2015 Q1 for Flights
df_airlines = spark.read.parquet("/mnt/mids-w261/datasets_final_project/parquet_airlines_data_3m/")

# Load the 2015 Q1 for Weather
df_weather = spark.read.parquet("/mnt/mids-w261/datasets_final_project/weather_data/*").filter(col('DATE') < "2015-04-01T00:00:00.000")


# Describe dataset sizes
print("\033[1mFull Datasets:\033[0m")
print(f"The full dataset for airlines contains {df_airlines_full.count()} records, with {len(df_airlines_full.columns)} columns.")
print(f"The full dataset for weather recordings contains {df_weather_full.count()} records, with {len(df_weather_full.columns)} columns.")
print(f"The NOAA weather station dataset contains {df_stations.count()} records, with {len(df_stations.columns)} columns.")

# Describe dataset sizes
print("\n")
print("\033[1mSubset Datasets:\033[0m")
print(f"The Q1 2015 dataset for ORD and ATL airports contains {df_airlines.count()} records, with {len(df_airlines.columns)} columns.")
print(f"The Q1 2015 NOAA dataset for weather recordings contains {df_weather.count()} records, with {len(df_weather.columns)} columns.")

Full Datasets: 
The full dataset for airlines contains 63493682 records, with 109 columns.
The full dataset for weather recordings contains 630904436 records, with 177 columns.
The NOAA weather station dataset contains 5004169 records, with 12 columns.


 Subset Datasets: 
The Q1 2015 dataset for ORD and ATL airports contains 161057 records, with 109 columns.
The Q1 2015 NOAA dataset for weather recordings contains 29823926 records, with 177 columns.

#### Airline Flight Data
We begin with the flights table in order to better understand the available features. To start, we examine the first 10 records, along with the provided schema.

In [0]:
display(df_airlines.limit(10))
df_airlines.printSchema()

YEAR QUARTER MONTH DAY_OF_MONTH DAY_OF_WEEK FL_DATE OP_UNIQUE_CARRIER OP_CARRIER_AIRLINE_ID OP_CARRIER TAIL_NUM OP_CARRIER_FL_NUM ORIGIN_AIRPORT_ID ORIGIN_AIRPORT_SEQ_ID ORIGIN_CITY_MARKET_ID ORIGIN ORIGIN_CITY_NAME ORIGIN_STATE_ABR ORIGIN_STATE_FIPS ORIGIN_STATE_NM ORIGIN_WAC DEST_AIRPORT_ID DEST_AIRPORT_SEQ_ID DEST_CITY_MARKET_ID DEST DEST_CITY_NAME DEST_STATE_ABR DEST_STATE_FIPS DEST_STATE_NM DEST_WAC CRS_DEP_TIME DEP_TIME DEP_DELAY DEP_DELAY_NEW DEP_DEL15 DEP_DELAY_GROUP DEP_TIME_BLK TAXI_OUT WHEELS_OFF WHEELS_ON TAXI_IN CRS_ARR_TIME ARR_TIME ARR_DELAY ARR_DELAY_NEW ARR_DEL15 ARR_DELAY_GROUP ARR_TIME_BLK CANCELLED CANCELLATION_CODE DIVERTED CRS_ELAPSED_TIME ACTUAL_ELAPSED_TIME AIR_TIME FLIGHTS DISTANCE DISTANCE_GROUP CARRIER_DELAY WEATHER_DELAY NAS_DELAY SECURITY_DELAY LATE_AIRCRAFT_DELAY FIRST_DEP_TIME TOTAL_ADD_GTIME LONGEST_ADD_GTIME DIV_AIRPORT_LANDINGS DIV_REACHED_DEST DIV_ACTUAL_ELAPSED_TIME DIV_ARR_DELAY DIV_DISTANCE DIV1_AIRPORT DIV1_AIRPORT_ID DIV1_AIRPORT_SEQ_ID DIV1_WHEELS_ON DIV1_TOTAL_GTIME DIV1_LONGEST_GTIME DIV1_WHEELS_OFF DIV1_TAIL_NUM DIV2_AIRPORT DIV2_AIRPORT_ID DIV2_AIRPORT_SEQ_ID DIV2_WHEELS_ON DIV2_TOTAL_GTIME DIV2_LONGEST_GTIME DIV2_WHEELS_OFF DIV2_TAIL_NUM DIV3_AIRPORT DIV3_AIRPORT_ID DIV3_AIRPORT_SEQ_ID DIV3_WHEELS_ON DIV3_TOTAL_GTIME DIV3_LONGEST_GTIME DIV3_WHEELS_OFF DIV3_TAIL_NUM DIV4_AIRPORT DIV4_AIRPORT_ID DIV4_AIRPORT_SEQ_ID DIV4_WHEELS_ON DIV4_TOTAL_GTIME DIV4_LONGEST_GTIME DIV4_WHEELS_OFF DIV4_TAIL_NUM DIV5_AIRPORT DIV5_AIRPORT_ID DIV5_AIRPORT_SEQ_ID DIV5_WHEELS_ON DIV5_TOTAL_GTIME DIV5_LONGEST_GTIME DIV5_WHEELS_OFF DIV5_TAIL_NUM 2015 1 2 1 7 2015-02-01 AA 19805 AA N3MEAA 392 13930 1393003 30977 ORD Chicago, IL IL 17 Illinois 41 12953 1295302 31703 LGA New York, NY NY 36 New York 22 730 749 19.0 19.0 1.0 1 0700-0759 34.0 823 1056 4.0 1030 1100 30.0 30.0 1.0 2 1000-1059 0.0 null 0.0 120.0 131.0 93.0 1.0 733.0 3 0.0 19.0 11.0 0.0 0.0 null null null 0 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null 2015 1 2 2 1 2015-02-02 AA 19805 AA N3LPAA 392 13930 1393003 30977 ORD Chicago, IL IL 17 Illinois 41 12953 1295302 31703 LGA New York, NY NY 36 New York 22 730 null null null null null 0700-0759 null null null null 1030 null null null null null 1000-1059 1.0 B 0.0 120.0 null null 1.0 733.0 3 null null null null null null null null 0 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null 2015 1 2 3 2 2015-02-03 AA 19805 AA N3LXAA 392 13930 1393003 30977 ORD Chicago, IL IL 17 Illinois 41 12953 1295302 31703 LGA New York, NY NY 36 New York 22 730 735 5.0 5.0 0.0 0 0700-0759 19.0 754 1027 9.0 1030 1036 6.0 6.0 0.0 0 1000-1059 0.0 null 0.0 120.0 121.0 93.0 1.0 733.0 3 null null null null null null null null 0 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null 2015 1 2 4 3 2015-02-04 AA 19805 AA N3LHAA 392 13930 1393003 30977 ORD Chicago, IL IL 17 Illinois 41 12953 1295302 31703 LGA New York, NY NY 36 New York 22 730 727 -3.0 0.0 0.0 -1 0700-0759 11.0 738 1008 5.0 1030 1013 -17.0 0.0 0.0 -2 1000-1059 0.0 null 0.0 120.0 106.0 90.0 1.0 733.0 3 null null null null null null null null 0 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null 2015 1 2 5 4 2015-02-05 AA 19805 AA N3LYAA 392 13930 1393003 30977 ORD Chicago, IL IL 17 Illinois 41 12953 1295302 31703 LGA New York, NY NY 36 New York 22 730 757 27.0 27.0 1.0 1 0700-0759 23.0 820 1058 3.0 1030 11

root
-- YEAR: integer (nullable = true)
-- QUARTER: integer (nullable = true)
-- MONTH: integer (nullable = true)
-- DAY_OF_MONTH: integer (nullable = true)
-- DAY_OF_WEEK: integer (nullable = true)
-- FL_DATE: string (nullable = true)
-- OP_UNIQUE_CARRIER: string (nullable = true)
-- OP_CARRIER_AIRLINE_ID: integer (nullable = true)
-- OP_CARRIER: string (nullable = true)
-- TAIL_NUM: string (nullable = true)
-- OP_CARRIER_FL_NUM: integer (nullable = true)
-- ORIGIN_AIRPORT_ID: integer (nullable = true)
-- ORIGIN_AIRPORT_SEQ_ID: integer (nullable = true)
-- ORIGIN_CITY_MARKET_ID: integer (nullable = true)
-- ORIGIN: string (nullable = true)
-- ORIGIN_CITY_NAME: string (nullable = true)
-- ORIGIN_STATE_ABR: string (nullable = true)
-- ORIGIN_STATE_FIPS: integer (nullable = true)
-- ORIGIN_STATE_NM: string (nullable = true)
-- ORIGIN_WAC: integer (nullable = true)
-- DEST_AIRPORT_ID: integer (nullable = true)
-- DEST_AIRPORT_SEQ_ID: integer (nullable = true)
-- DEST_CITY_MARKET_ID: integer (nullable = true)
-- DEST: string (nullable = true)
-- DEST_CITY_NAME: string (nullable = true)
-- DEST_STATE_ABR: string (nullable = true)
-- DEST_STATE_FIPS: integer (nullable = true)
-- DEST_STATE_NM: string (nullable = true)
-- DEST_WAC: integer (nullable = true)
-- CRS_DEP_TIME: integer (nullable = true)
-- DEP_TIME: integer (nullable = true)
-- DEP_DELAY: double (nullable = true)
-- DEP_DELAY_NEW: double (nullable = true)
-- DEP_DEL15: double (nullable = true)
-- DEP_DELAY_GROUP: integer (nullable = true)
-- DEP_TIME_BLK: string (nullable = true)
-- TAXI_OUT: double (nullable = true)
-- WHEELS_OFF: integer (nullable = true)
-- WHEELS_ON: integer (nullable = true)
-- TAXI_IN: double (nullable = true)
-- CRS_ARR_TIME: integer (nullable = true)
-- ARR_TIME: integer (nullable = true)
-- ARR_DELAY: double (nullable = true)
-- ARR_DELAY_NEW: double (nullable = true)
-- ARR_DEL15: double (nullable = true)
-- ARR_DELAY_GROUP: integer (nullable = true)
-- ARR_TIME_BLK: string (nullable = true)
-- CANCELLED: double (nullable = true)
-- CANCELLATION_CODE: string (nullable = true)
-- DIVERTED: double (nullable = true)
-- CRS_ELAPSED_TIME: double (nullable = true)
-- ACTUAL_ELAPSED_TIME: double (nullable = true)
-- AIR_TIME: double (nullable = true)
-- FLIGHTS: double (nullable = true)
-- DISTANCE: double (nullable = true)
-- DISTANCE_GROUP: integer (nullable = true)
-- CARRIER_DELAY: double (nullable = true)
-- WEATHER_DELAY: double (nullable = true)
-- NAS_DELAY: double (nullable = true)
-- SECURITY_DELAY: double (nullable = true)
-- LATE_AIRCRAFT_DELAY: double (nullable = true)
-- FIRST_DEP_TIME: integer (nullable = true)
-- TOTAL_ADD_GTIME: double (nullable = true)
-- LONGEST_ADD_GTIME: double (nullable = true)
-- DIV_AIRPORT_LANDINGS: integer (nullable = true)
-- DIV_REACHED_DEST: double (nullable = true)
-- DIV_ACTUAL_ELAPSED_TIME: double (nullable = true)
-- DIV_ARR_DELAY: double (nullable = true)
-- DIV_DISTANCE: double (nullable = true)
-- DIV1_AIRPORT: string (nullable = true)
-- DIV1_AIRPORT_ID: integer (nullable = true)
-- DIV1_AIRPORT_SEQ_ID: integer (nullable = true)
-- DIV1_WHEELS_ON: integer (nullable = true)
-- DIV1_TOTAL_GTIME: double (nullable = true)
-- DIV1_LONGEST_GTIME: double (nullable = true)
-- DIV1_WHEELS_OFF: integer (nullable = true)
-- DIV1_TAIL_NUM: string (nullable = true)
-- DIV2_AIRPORT: string (nullable = true)
-- DIV2_AIRPORT_ID: integer (nullable = true)
-- DIV2_AIRPORT_SEQ_ID: integer (nullable = true)
-- DIV2_WHEELS_ON: integer (nullable = true)
-- DIV2_TOTAL_GTIME: double (nullable = true)
-- DIV2_LONGEST_GTIME: double (nullable = true)
-- DIV2_WHEELS_OFF: integer (nullable = true)
-- DIV2_TAIL_NUM: string (nullable = true)
-- DIV3_AIRPORT: string (nullable = true)
-- DIV3_AIRPORT_ID: integer (nullable = true)
-- DIV3_AIRPORT_SEQ_ID: integer (nullable = true)
-- DIV3_WHEELS_ON: integer (nullable = true)
-- DIV3_TOTAL_GTIME: double (nullable = true)
-- DIV3_LONGEST_GTIME: double (nullable = true)
-- DIV3_WHEELS_

**Airline Data Cleaning Summary**

The airlines dataset is robust, however, some features are unnecessary for our purpose. An overview of the cleaning steps for the airline table are as follows:

1. Feature removal
  - Alternative names for airline carriers, airports, cities, and states removed, leaving OP_UNIQUE_CARRIER, ORIGIN/DEST_AIRPORT_ID, ORIGIN/DEST, ORIGIN/DEST_STATE_ABR, ORIGIN/DEST_CITY_NAME 
  - Removed information about dept, 2nd, 3rd, 4th, and 5th diverted flights, because we're only looking at whether a flight is or is not 15 minutes delayed. Any diversion is going to knock a flight more than 15 minutes off track, and the 4th and 5th diverted flights are all NULL in the 3mo dataset.
  - Removed additional gate departure time columns as that departure time is built into the departure delay.

2. Feature combinations
  - To make up for removing the information about the specific diverted flights, we added the diverted flight arrival delays into the arrival delay. Diverted delays previously had their own column and now they're combined. We know where the delay is from based on the diverted column showing 1 or 0.
  - Cancellations were added as delays into the outcome variable dep_is_delayed, with a separate indicator variable

3. Null Values
  - The NULL values are generally where canceled flights do not have a departure time. At this stage, we are not filling nulls.

4. Duplicate values
  - Duplicate values are dropped. These were not present in the three month dataset, but did exist in the full dataset.

5. Additional datasets and timezones
  - The dataset uses local timezone and does not have the same airport code type as our weather data, so a publically available Open Airlines dataset which has both timezones and the ICAO airport codes is joined
  - Finally, the timezones are used to generate the "time_at_prediction_utc" feature, which is the timestamp used when predicting delays (2 hours before the planned departure).
6. Indexing
  - An index is created for more efficient joining, sorting, and processing based on the flight date, departure time, and airplane tail number

Below, we lay out the function for cleaning the data:

In [0]:
def clean_airline_data(df):
  # drop duplicate entries and create temporary view of airlines data
  df.drop_duplicates().createOrReplaceTempView('df_tmp')
  
  # load OpenAirlines data for ICAO code and Timezone
  df_open_airlines = spark.read.csv('dbfs:/FileStore/shared_uploads/mbollig@berkeley.edu/airports.dat', header=False, inferSchema= False)\
                          .toDF("airport_id", "name", "city", "country", "IATA", "ICAO", "latitude", "longitude", "altitude", "utc_offset", "DST", "timezone", "type", "source")
    
  # create temporary view of OpenAirlines data
  df_open_airlines.createOrReplaceTempView('open_airlines')
  
  # structure query to change data types, add open_airlines, removed and combine base features, and change timezones
  query = '''
          
  SELECT 
     ROW_NUMBER() OVER (ORDER BY FL_DATE, DEP_TIME, TAIL_NUM) as index_id
     , string(oao.ICAO) as origin_ICAO
     , cast(oao.utc_offset as INTEGER) as origin_utc_offset
     , oao.timezone as origin_timezone
     , oao.latitude as origin_latitude
     , oao.longitude as origin_longitude
     , oao.altitude as origin_altitude
     , string(oad.ICAO) as dest_ICAO
     , cast(oad.utc_offset as INTEGER) as dest_utc_offset
     , oad.timezone as dest_timezone
     , oad.latitude as dest_latitude
     , oad.longitude as dest_longitude
     , oad.altitude as dest_altitude
     , string(YEAR) as year
     , string(QUARTER) as quarter
     , string(MONTH) as month
     , string(DAY_OF_MONTH) as day_of_month
     , string(DAY_OF_WEEK) as day_of_week
     , FL_DATE as dt                                  -- date of flight departure
     , string(OP_UNIQUE_CARRIER) as carrier
     , string(TAIL_NUM) as tail_num
     , string(OP_CARRIER_FL_NUM) as flight_num
     , ORIGIN_STATE_ABR as origin_state
     , ORIGIN_CITY_NAME as origin_city
     , string(ORIGIN_AIRPORT_ID) as origin_airport_id         -- airport codes can change, this stays constant
     , string(ORIGIN) as origin_airport_code
     , DEST_STATE_ABR as dest_state
     , DEST_CITY_NAME as dest_city
     , string(DEST_AIRPORT_ID) as dest_airport_id
     , string(DEST) as dest_airport_code
     , CASE
         WHEN LENGTH(CRS_DEP_TIME) = 1 THEN CONCAT('000', CRS_DEP_TIME)
         WHEN LENGTH(CRS_DEP_TIME) = 2 THEN CONCAT('00', CRS_DEP_TIME)
         WHEN LENGTH(CRS_DEP_TIME) = 3 THEN CONCAT('0', CRS_DEP_TIME)
         WHEN CRS_DEP_TIME = 2400 THEN 2359       -- 2400 is not a valid HHMM, moving back 1 minute
         ELSE CRS_DEP_TIME
       END as planned_dep_time
     , DEP_TIME as actual_dep_time
     , IFNULL(DEP_DELAY, 0) as delay_minutes                  -- negatives mean early
     , string(CASE
         WHEN CANCELLED = 1 THEN 1
         ELSE DEP_DEL15
       END) as dep_is_delayed                 -- OUTCOME VARIABLE, includes cancelled flights as 1 as well
     , string(DEP_DELAY_GROUP) as dep_delay_group
     , string(DEP_TIME_BLK) as dep_hour
     , ARR_TIME as actual_arr_time
     , CASE
         WHEN DIV_ARR_DELAY IS NOT NULL THEN DIV_ARR_DELAY    -- added diverted delays to arrival delays
         ELSE ARR_DELAY
       END as arr_delay_minutes                    -- negatives mean early (now includes diverted flights)
     , string(ARR_DELAY_GROUP) as arr_delay_group
     , string(ARR_TIME_BLK) as arr_hour
     , boolean(CANCELLED) as canceled
     , string(CANCELLATION_CODE) as cancel_code            -- B = weather, A = airline, C = National Air System, D = security
     , boolean(DIVERTED) as is_diverted
     , CRS_ELAPSED_TIME as planned_duration
     , ACTUAL_ELAPSED_TIME as actual_duration
     , FLIGHTS as num_flights
     , DISTANCE as flight_distance
     , string(DISTANCE_GROUP) as distance_group
     , CARRIER_DELAY as carrier_delay
     , WEATHER_DELAY as weather_delay
     , NAS_DELAY as nas_delay
     , SECURITY_DELAY as security_delay
     , LATE_AIRCRAFT_DELAY as late_aircraft_delay
     -- not including gate_departure info for flights that returned to the gate since wrapped up in delay times for previous flights
     , boolean(DIV_REACHED_DEST) as div_reached_dest
     -- not including most diverted information as not super relevant outside of knowing that it was diverted and adding the diverted arrival delay to the arrival_delay column
  FROM {0} a
  LEFT JOIN {1} oao
    ON oao.IATA = ORIGIN
  LEFT JOIN {1} oad
    ON oad.IATA = DEST

'''.format('df_tmp', 'open_airlines')

  
  # add timezones
  df_with_tz = spark.sql(query)\
      .withColumn('planned_departure_utc',
                  to_utc_timestamp(to_timestamp(concat(col('dt'), col('planned_dep_time')), 'yyyy-MM-ddHHmm'), col('origin_timezone')))\
      .withColumn('time_at_prediction_utc',
                  to_utc_timestamp(to_timestamp(concat(col('dt'), col('planned_dep_time')), 'yyyy-MM-ddHHmm'), col('origin_timezone'))\
                  + expr('INTERVAL -2 HOURS'))\
  
  return df_with_tz

This function is used to clean the subset 3 month dataset, as well as the full airlines data. We save these intermediate tables for efficiency.

In [0]:
# clean the 3 month dataset
df_airlines_clean = clean_airline_data(df_airlines)

# write to parquet
df_airlines_clean.write.mode('overwrite').parquet(f"{blob_url}/airlines_eda_v1")

# clean full dataset
df_airlines_full_clean = clean_airline_data(df_airlines_full)

# write intermediate table
df_airlines_full_clean.write.mode('overwrite').parquet(f"{blob_url}/airlines_clean_full_v1")

In [0]:
# display
display(df_airlines_clean_full.limit(10))

index_id origin_ICAO origin_utc_offset origin_timezone origin_latitude origin_longitude origin_altitude dest_ICAO dest_utc_offset dest_timezone dest_latitude dest_longitude dest_altitude year quarter month day_of_month day_of_week dt carrier tail_num flight_num origin_state origin_city origin_airport_id origin_airport_code dest_state dest_city dest_airport_id dest_airport_code planned_dep_time actual_dep_time delay_minutes dep_is_delayed dep_delay_group dep_hour actual_arr_time arr_delay_minutes arr_delay_group arr_hour canceled cancel_code is_diverted planned_duration actual_duration num_flights flight_distance distance_group carrier_delay weather_delay nas_delay security_delay late_aircraft_delay div_reached_dest planned_departure_utc time_at_prediction_utc 1 KMSO -7 America/Denver 46.91630173 -114.0910034 3206 KDEN -7 America/Denver 39.861698150635 -104.672996521 5431 2015 1 1 1 4 2015-01-01 F9 null 865 MT Missoula, MT 13486 MSO CO Denver, CO 11292 DEN 0600 null 0.0 true null 0600-0659 null null null 0800-0859 true A false 120.0 null 1.0 679.0 3 null null null null null null 2015-01-01T13:00:00.000+0000 2015-01-01T11:00:00.000+0000 2 KMSO -7 America/Denver 46.91630173 -114.0910034 3206 KDEN -7 America/Denver 39.861698150635 -104.672996521 5431 2015 1 1 1 4 2015-01-01 F9 null 865 MT Missoula, MT 13486 MSO CO Denver, CO 11292 DEN 0600 null 0.0 true null 0600-0659 null null null 0800-0859 true A false 120.0 null 1.0 679.0 3 null null null null null null 2015-01-01T13:00:00.000+0000 2015-01-01T11:00:00.000+0000 3 KORD -6 America/Chicago 41.9786 -87.9048 672 KMIA -5 America/New_York 25.79319953918457 -80.29060363769531 8 2015 1 1 1 4 2015-01-01 F9 null 1256 IL Chicago, IL 13930 ORD FL Miami, FL 13303 MIA 0600 null 0.0 true null 0600-0659 null null null 1000-1059 true A false 180.0 null 1.0 1197.0 5 null null null null null null 2015-01-01T12:00:00.000+0000 2015-01-01T10:00:00.000+0000 4 KORD -6 America/Chicago 41.9786 -87.9048 672 KMIA -5 America/New_York 25.79319953918457 -80.29060363769531 8 2015 1 1 1 4 2015-01-01 F9 null 1256 IL Chicago, IL 13930 ORD FL Miami, FL 13303 MIA 0600 null 0.0 true null 0600-0659 null null null 1000-1059 true A false 180.0 null 1.0 1197.0 5 null null null null null null 2015-01-01T12:00:00.000+0000 2015-01-01T10:00:00.000+0000 5 KMIA -5 America/New_York 25.79319953918457 -80.29060363769531 8 KORD -6 America/Chicago 41.9786 -87.9048 672 2015 1 1 1 4 2015-01-01 F9 null 1257 FL Miami, FL 13303 MIA IL Chicago, IL 13930 ORD 1050 null 0.0 true null 1000-1059 null null null 1300-1359 true A false 200.0 null 1.0 1197.0 5 null null null null null null 2015-01-01T15:50:00.000+0000 2015-01-01T13:50:00.000+0000 6 KMIA -5 America/New_York 25.79319953918457 -80.29060363769531 8 KORD -6 America/Chicago 41.9786 -87.9048 672 2015 1 1 1 4 2015-01-01 F9 null 1257 FL Miami, FL 13303 MIA IL Chicago, IL 13930 ORD 1050 null 0.0 true null 1000-1059 null null null 1300-1359 true A false 200.0 null 1.0 1197.0 5 null null null null null null 2015-01-01T15:50:00.000+0000 2015-01-01T13:50:00.000+0000 7 KDEN -7 America/Denver 39.861698150635 -104.672996521 5431 KMSP -6 America/Chicago 44.882 -93.221802 841 2015 1 1 1 4 2015-01-01 UA null 215 CO Denver, CO 11292 DEN MN Minneapolis, MN 13487 MSP 1953 null 0.0 true null 1900-1959 null null null 2200-2259 true B false 116.0 null 1.0 680.0 3 null null null null null null 2015-01-02T02:53:00.000+0000 2015-01-02T00:53:00.000+0000 8 KDEN -7 America/Denver 39.861698150635 -104.672996521 5431 KMSP -6 America/Chicago 44.882 -93.221802 841 2015 1 1 1 4 2015-01-01 UA null 215 CO Denver, CO 11292 DEN MN Minneapolis, MN 13487 MSP 1953 null 0.0 true null 1900-1959 null null null 2200-2259 true B false 116.0 null 1.0 680.0 3 null null null null null null 2015-01-02T02:53:00.000+0000 2015-01-02T00:53:00.000+0000 9 KSLC -7 America/Denver 40.78839874267578 -111.97799682617188 4227 KPHL -5 America/New_York 39.87189865112305 -75.24109649658203 36 2015 1 1 1 4 2015-01-01 US null 1883 UT Salt Lake Cit

#### Weather Station Location Data
Next, we explored the weather station table to better understand the available features. To start, the first 10 records are printed, as well as the provided schema.

In [0]:
display(df_stations.limit(10))
df_stations.printSchema()

usaf wban station_id lat lon neighbor_id neighbor_name neighbor_state neighbor_call neighbor_lat neighbor_lon distance_to_neighbor 690020 93218 69002093218 36.0 -121.233 69002093218 JOLON HUNTER LIGGETT MIL RES CA KHGT 36.0 -121.233 0.0 690020 93218 69002093218 36.0 -121.233 69007093217 FRITZSCHE AAF CA KOAR 36.683 -121.767 55.73024537916726 690020 93218 69002093218 36.0 -121.233 69014093101 EL TORO MCAS CA KNZJ 33.667 -117.733 255.49106220353934 690020 93218 69002093218 36.0 -121.233 70027127506 BARROW POINT BARROW AK KPBA 71.333 -156.65 2750.4353299559803 690020 93218 69002093218 36.0 -121.233 70045027512 LONELY AK LNI 70.917 -153.25 2676.3554370627153 690020 93218 69002093218 36.0 -121.233 70063027403 OLIKTOK POW 2 AK POLI 70.5 -149.883 2604.050248854232 690020 93218 69002093218 36.0 -121.233 70063526465 GALBRAITH LAKE AIRPORT AK PAGB 68.479 -149.49 2490.9756094472277 690020 93218 69002093218 36.0 -121.233 70063627405 PRUDHOE BAY AK PAUD 70.25 -148.333 2568.180281844432 690020 93218 69002093218 36.0 -121.233 70104626418 CENTRAL AIRPORT AK PACE 65.567 -144.765 2254.5584891291946 690020 93218 69002093218 36.0 -121.233 70119526625 SHISHMAREF/NEW AIRPORT AK PASH 66.25 -166.089 2743.6881828292408

root
-- usaf: string (nullable = true)
-- wban: string (nullable = true)
-- station_id: string (nullable = true)
-- lat: double (nullable = true)
-- lon: double (nullable = true)
-- neighbor_id: string (nullable = true)
-- neighbor_name: string (nullable = true)
-- neighbor_state: string (nullable = true)
-- neighbor_call: string (nullable = true)
-- neighbor_lat: double (nullable = true)
-- neighbor_lon: double (nullable = true)
-- distance_to_neighbor: double (nullable = true)

**Station Data Cleaning Summary**

The station data is not time-dependent, so there is no smaller subset to test on. This dataset is primarily used to link the flights data to the airlines data. In order to make joining more efficient, the following cleaning steps were taken:

1. Feature removal
  - Removed all featuers except for the weather station ID and the ICAO code that will be used to join to the Airlines/OpenAirlines dataset.

2. Filtering
  - Filtered out all stations that had a 'distance_to_neighbor' of greater than 0, removing all weather stations not located the recorded ICAO airport location.

In [0]:
# clean station data
df_stations_clean = df_stations.filter(col("distance_to_neighbor") == 0).select('station_id','neighbor_call')

# display
display(df_stations_clean.limit(10))

# write full dataset
df_stations_clean.write.mode('overwrite').parquet(f"{blob_url}/stations_clean_full")

station_id neighbor_call 69002093218 KHGT 69007093217 KOAR 69014093101 KNZJ 70027127506 KPBA 70045027512 LNI 70063027403 POLI 70063526465 PAGB 70063627405 PAUD 70104626418 PACE 70119526625 PASH

#### Weather Observation Data
Next, we'll take a peek at our NOAA [weather dataset](https://www.ncdc.noaa.gov/orders/qclcd/)

Because we started our data exploration with just the 3 month data to make it faster, we subsetted our weather data to just ATL and ORD since our 3 month airlines dataset is also subsetted to only departures from those airlines. Subsetting this dataset here, and in the full dataset speeds up the join considerably. The full dataset contains all of the weather stations around the world, and, as you'll see later, we subset it to only include weather stations in the US.

In [0]:
display(df_weather_full.limit(10))

STATION DATE SOURCE LATITUDE LONGITUDE ELEVATION NAME REPORT_TYPE CALL_SIGN QUALITY_CONTROL WND CIG VIS TMP DEW SLP AW1 GA1 GA2 GA3 GA4 GE1 GF1 KA1 KA2 MA1 MD1 MW1 MW2 OC1 OD1 OD2 REM EQD AW2 AX4 GD1 AW5 GN1 AJ1 AW3 MK1 KA4 GG3 AN1 RH1 AU5 HL1 OB1 AT8 AW7 AZ1 CH1 RH3 GK1 IB1 AX1 CT1 AK1 CN2 OE1 MW5 AO1 KA3 AA3 CR1 CF2 KB2 GM1 AT5 AY2 MW6 MG1 AH6 AU2 GD2 AW4 MF1 AA1 AH2 AH3 OE3 AT6 AL2 AL3 AX5 IB2 AI3 CV3 WA1 GH1 KF1 CU2 CT3 SA1 AU1 KD2 AI5 GO1 GD3 CG3 AI1 AL1 AW6 MW4 AX6 CV1 ME1 KC2 CN1 UA1 GD5 UG2 AT3 AT4 GJ1 MV1 GA5 CT2 CG2 ED1 AE1 CO1 KE1 KB1 AI4 MW3 KG2 AA2 AX2 AY1 RH2 OE2 CU3 MH1 AM1 AU4 GA6 KG1 AU3 AT7 KD1 GL1 IA1 GG2 OD3 UG1 CB1 AI6 CI1 CV2 AZ2 AD1 AH1 WD1 AA4 KC1 IA2 CF3 AI2 AT1 GD4 AX3 AH4 KB3 CU1 CN4 AT2 CG1 CF1 GG1 MV2 CW1 GG4 AB1 AH5 CN3 7650099999 2016-01-01T00:00:00.000+0000 4 43.435555 5.213611 22.55 PROVENCE, FR FM-12 99999 V020 190,1,N,0015,1 99999,9,9,N 007000,1,9,9 +0101,1 +0090,1 10255,1 99,9,+02250,1,99,9 9,AGL ,+99999,+99999 08,99,1,99,9,99,9,02250,1,99,9,99,9 99999,9,10216,1 8,1,004,1,+999,9 61,1 3,99,0026,1,999 SYN09807650 04857 81903 10101 20090 30216 40255 58004 69901 761// 333 4/000 69907 90710 91105 555 69905= 9999,1,9,999999,9,9 03,0000,2,1 06,0000,2,1 7650099999 2016-01-01T00:00:00.000+0000 4 43.435555 5.213611 22.55 PROVENCE, FR FM-15 99999 V020 190,1,N,0015,1 22000,1,9,N 009000,1,9,9 +0100,1 +0090,1 99999,9 61,1 00,99,1,99,9,99,9,99999,9,99,9,99,9 10250,1,99999,9 MET057METAR LFML 010000Z AUTO 19003KT 9000 -RA NSC 10/09 Q1025= 7650099999 2016-01-01T00:30:00.000+0000 4 43.435555 5.213611 22.55 PROVENCE, FR FM-15 99999 V020 250,1,N,0010,1 99999,9,9,N 008000,1,9,9 +9999,9 +9999,9 99999,9 10250,1,99999,9 MET056METAR LFML 010030Z AUTO 25002KT 8000 ///TCU 10/09 Q1025= Q019 2ATOD 7650099999 2016-01-01T01:00:00.000+0000 4 43.435555 5.213611 22.55 PROVENCE, FR FM-12 99999 V020 999,9,C,0000,1 99999,9,9,N 004900,1,9,9 +0099,1 +0094,1 10251,1 99,9,+02250,1,99,9 9,AGL ,+99999,+99999 08,99,1,99,9,99,9,02250,1,99,9,99,9 99999,9,10212,1 8,1,006,1,+999,9 10,1 3,99,0015,1,999 SYN07607650 24849 80000 10099 20094 30212 40251 58006 710// 333 69925 90710 91103= 01,0002,3,1 7650099999 2016-01-01T01:00:00.000+0000 4 43.435555 5.213611 22.55 PROVENCE, FR FM-15 99999 V020 999,9,C,0000,1 22000,1,9,N 007000,1,9,9 +0100,1 +0090,1 99999,9 00,99,1,99,9,99,9,99999,9,99,9,99,9 10250,1,99999,9 MET053METAR LFML 010100Z AUTO 00000KT 7000 NSC 10/09 Q1025= 7650099999 2016-01-01T01:30:00.000+0000 4 43.435555 5.213611 22.55 PROVENCE, FR FM-15 99999 V020 999,9,C,0000,1 22000,1,9,N 009000,1,9,9 +0100,1 +0090,1 99999,9 00,99,1,99,9,99,9,99999,9,99,9,99,9 10250,1,99999,9 MET053METAR LFML 010130Z AUTO 00000KT 9000 NSC 10/09 Q1025= 7650099999 2016-01-01T02:00:00.000+0000 4 43.435555 5.213611 22.55 PROVENCE, FR FM-12 99999 V020 999,9,C,0000,1 99999,9,9,N 011000,1,9,9 +0100,1 +0088,1 10254,1 99,9,+01750,1,99,9 9,AGL ,+99999,+99999 08,99,1,99,9,99,9,01750,1,99,9,99,9 99999,9,10215,1 5,1,005,1,+999,9 00,1 3,99,0010,1,999 SYN07607650 24761 80000 10100 20088 30215 40254 55005 700// 333 60005 90710 91102= 01,0000,9,1 7650099999 2016-01-01T02:00:00.000+0000 4 43.435555 5.213611 22.55 PROVENCE, FR FM-15 99999 V020 999,9,C,0000,1 99999,9,9,Y 999999,9,9,9 +0100,1 +0090,1 99999,9 10250,1,99999,9 MET050METAR LFML 010200Z AUTO 00000KT CAVOK 10/09 Q1025= 7650099999 2016-01-01T02:30:00.000+0000 4 43.435555 5.213611 22.55 PROVENCE, FR FM-15 99999 V020 320,1,N,0015,1 22000,1,9,N 008000,1,9,9 +0100,1 +0090,1 99999,9 00,99,1,99,9,99,9,99999,9,99,9,99,9 10250,1,99999,9 MET053METAR LFML 010230Z AUTO 32003KT 8000 NSC 10/09 Q1025= 7650099999 2016-01-01T03:00:00.000+0000 4 43.435555 5.213611 22.55 PROVENCE, FR FM-12 99999 V020 040,1,N,0010,1 01500,1,9,N 006000,1,9,9 +0099,1 +0093,1 10253,1 07,1,+01500,1,06,1 9,AGL ,+99999,+99999 07,99,1,07,1,99,9,01500,1,99,9,99,9 99999,9,10214,1 6,1,002,1,+999,9 3,99,0021,1,999 SYN09207650 22756 70402 10099 20093 30214 40253 56002 875// 333 69927 87650 90710 91104 555 60005= 03,0002,3,1

In [0]:
def replace(column, value):
  return when(column != value, column).otherwise(lit(None))

def unpack_and_clean_weather(df, origin_stations):
  # drop measurements from irrelevant locations
  df = df.filter(col('STATION').isin(origin_stations))
  
  # split columns
  df = df.select(df.STATION,
                 df.DATE,
                 df.LATITUDE,
                 df.LONGITUDE,
                 df.NAME,
                 split(df.WND, ',').alias("split_wnd"),
                 split(df.CIG, ',').alias("split_cig"),
                 split(df.VIS, ',').alias("split_vis"),
                 split(df.TMP, ',').alias("split_tmp"),
                 split(df.DEW, ',').alias("split_dew"),
                 split(df.SLP, ',').alias("split_slp"))

  
  # add columns and replace missing values with null
  df_weather_clean = df.select(df.STATION,
                               df.DATE,
                               df.LATITUDE,
                               df.LONGITUDE,
                               df.NAME,
                               df.split_wnd.getItem(0).alias('WND_ANGLE'),
                               df.split_wnd.getItem(1).alias('WND_ANGLE_QC'),
                               df.split_wnd.getItem(2).alias('WND_TYPE'),
                               replace(df.split_wnd.getItem(3), "9999").cast(IntegerType()).alias('WND_SPEED'),
                               df.split_wnd.getItem(4).alias('WND_SPEED_QC'),
                               replace(df.split_cig.getItem(0), "99999").cast(IntegerType()).alias('CIG_CLOUD_AGL'),
                               df.split_cig.getItem(1).alias('CIG_CLOUD_AGL_QC'),
                               df.split_cig.getItem(2).alias('CIG_METHOD'),
                               replace(df.split_cig.getItem(3), "9").alias('CIG_CAVOK'),
                               replace(df.split_vis.getItem(0), "999999").cast(IntegerType()).alias('VIS_DIST'),
                               df.split_vis.getItem(1).alias('VIS_DIST_QC'),
                               df.split_vis.getItem(2).alias('VIS_VAR'),
                               df.split_vis.getItem(3).alias('VIS_VAR_QC'),
                               replace(df.split_tmp.getItem(0), "+9999").cast(IntegerType()).alias('TMP_C'),
                               df.split_tmp.getItem(1).alias('TMP_QC'),
                               replace(df.split_dew.getItem(0), "+9999").cast(IntegerType()).alias('DEW_C'),
                               df.split_dew.getItem(1).alias('DEW_QC'),
                               replace(df.split_slp.getItem(0), "99999").cast(IntegerType()).alias('SLP_P'),
                               df.split_slp.getItem(1).alias('SLP_QC'),
                              )

  return df_weather_clean

We test this on the 3 month subset data:

In [0]:
# list unique origin airports
origin_ICAO = [row[0] for row in df_airlines_clean.select(col('origin_ICAO')).dropDuplicates().collect()]

# list stations ids of unique origin airports
origin_stations = [row[0] for row in df_stations_clean.filter(col('neighbor_call').isin(origin_ICAO)).select(col('station_id')).dropDuplicates().collect()]

# subset for relevant airports and clean
df_weather_clean = unpack_and_clean_weather(df_weather, origin_stations)

# write
df_weather_clean.write.mode('overwrite').parquet(f"{blob_url}/weather_eda_v1")

# display
display(df_weather_clean.limit(10))

STATION DATE LATITUDE LONGITUDE NAME WND_ANGLE WND_ANGLE_QC WND_TYPE WND_SPEED WND_SPEED_QC CIG_CLOUD_AGL CIG_CLOUD_AGL_QC CIG_METHOD CIG_CAVOK VIS_DIST VIS_DIST_QC VIS_VAR VIS_VAR_QC TMP_C TMP_QC DEW_C DEW_QC SLP_P SLP_QC 72530094846 2015-01-01T00:00:00.000+0000 41.995 -87.9336 CHICAGO OHARE INTERNATIONAL AIRPORT, IL US 240 1 N 62 1 null 9 9 N 16000 1 9 9 -83 1 -172 1 10243 1 72530094846 2015-01-01T00:51:00.000+0000 41.995 -87.9336 CHICAGO OHARE INTERNATIONAL AIRPORT, IL US 240 5 N 57 5 22000 5 9 N 16093 5 N 5 -78 5 -172 5 10234 5 72530094846 2015-01-01T01:51:00.000+0000 41.995 -87.9336 CHICAGO OHARE INTERNATIONAL AIRPORT, IL US 230 5 N 77 5 22000 5 9 N 16093 5 N 5 -78 5 -167 5 10235 5 72530094846 2015-01-01T02:51:00.000+0000 41.995 -87.9336 CHICAGO OHARE INTERNATIONAL AIRPORT, IL US 240 5 N 72 5 22000 5 9 N 16093 5 N 5 -78 5 -172 5 10232 5 72530094846 2015-01-01T03:51:00.000+0000 41.995 -87.9336 CHICAGO OHARE INTERNATIONAL AIRPORT, IL US 240 5 N 67 5 22000 5 9 N 16093 5 N 5 -78 5 -172 5 10229 5 72530094846 2015-01-01T04:51:00.000+0000 41.995 -87.9336 CHICAGO OHARE INTERNATIONAL AIRPORT, IL US 240 5 N 88 5 22000 5 9 N 16093 5 N 5 -78 5 -172 5 10223 5 72530094846 2015-01-01T05:51:00.000+0000 41.995 -87.9336 CHICAGO OHARE INTERNATIONAL AIRPORT, IL US 250 5 N 62 5 22000 5 9 N 16093 5 N 5 -83 5 -167 5 10212 5 72530094846 2015-01-01T05:59:00.000+0000 41.995 -87.9336 CHICAGO OHARE INTERNATIONAL AIRPORT, IL US 999 9 9 null 9 null 9 9 null null 9 9 9 null 9 null 9 null 9 72530094846 2015-01-01T05:59:00.000+0000 41.995 -87.9336 CHICAGO OHARE INTERNATIONAL AIRPORT, IL US 999 9 9 null 9 null 9 9 null null 9 9 9 null 9 null 9 null 9 72530094846 2015-01-01T06:00:00.000+0000 41.995 -87.9336 CHICAGO OHARE INTERNATIONAL AIRPORT, IL US 250 1 N 62 1 null 9 9 N 16000 1 9 9 -83 1 -167 1 10212 1

We apply it to the full weather data

In [0]:
# list unique origin airports
origin_ICAO_full = [row[0] for row in df_airlines_clean_full.select(col('origin_ICAO')).dropDuplicates().collect()]

# list stations ids of unique origin airports
origin_stations_full = [row[0] for row in df_stations_clean.filter(col('neighbor_call').isin(origin_ICAO_full)).select(col('station_id')).dropDuplicates().collect()]

# clean full dataset
df_weather_full_clean = unpack_and_clean_weather(df_weather_full, origin_stations_full)

# write
df_weather_full_clean.write.mode('overwrite').parquet(f"{blob_url}/weather_clean_full_v1")

In [0]:
# size savings
print(f"Number of weather records (raw weather data): {df_weather_full.count()}")
print(f"Number of weather records from origin airports (cleaned weather data): {df_weather_full_clean.count()}")

Number of weather records (raw weather data): 630904436
Number of weather records from origin airports (cleaned weather data): 23970618

### Section 2 - Joining the data

#### Stations to Airlines
Due to the ICAO codes joined to the airlines from the OpenAirlines data sources, this join is straightforward. The stations data may be joined by this code (`neighbor_call` to `ICAO`). This is done twice: once for the origin stations and once for the destination stations.

In [0]:
def join_stations_to_airlines(airlines, stations):
  # subset and rename
  stations = stations.select(col("neighbor_call"),
                             col("station_id").alias(f"origin_station_id"),
                             col("station_id").alias(f"dest_station_id"))
  
  # join
  joined = airlines.alias('a').join(stations.alias('so'),
                                    col("a.origin_ICAO") == col("so.neighbor_call"), 'left')\
                              .join(stations.alias('sd'),
                                    col("a.dest_ICAO") == col("sd.neighbor_call"), 'left')\
                              .select('a.*', 'so.origin_station_id', 'sd.dest_station_id')
  
  return joined

Again, we test the function on the subset 3 month dataset:

In [0]:
# read if necessary
df_airlines_clean = spark.read.parquet(f"{blob_url}/airlines_eda_v1/*")
df_stations_clean = spark.read.parquet(f"{blob_url}/stations_clean_full/*")

# join
df_airlines_stations = join_stations_to_airlines(df_airlines_clean, df_stations_clean)
display(df_airlines_stations.limit(10))

# write
df_airlines_stations.write.mode('overwrite').parquet(f"{blob_url}/airlines_stations_v0")

index_id origin_ICAO origin_utc_offset origin_timezone origin_latitude origin_longitude origin_altitude dest_ICAO dest_utc_offset dest_timezone dest_latitude dest_longitude dest_altitude year quarter month day_of_month day_of_week dt carrier tail_num flight_num origin_state origin_city origin_airport_id origin_airport_code dest_state dest_city dest_airport_id dest_airport_code planned_dep_time actual_dep_time delay_minutes dep_is_delayed dep_delay_group dep_hour actual_arr_time arr_delay_minutes arr_delay_group arr_hour canceled cancel_code is_diverted planned_duration actual_duration num_flights flight_distance distance_group carrier_delay weather_delay nas_delay security_delay late_aircraft_delay div_reached_dest planned_departure_utc time_at_prediction_utc origin_station_id dest_station_id 1 KORD -6 America/Chicago 41.9786 -87.9048 672 KMIA -5 America/New_York 25.79319953918457 -80.29060363769531 8 2015 1 1 1 4 2015-01-01 F9 null 1256 IL Chicago, IL 13930 ORD FL Miami, FL 13303 MIA 0600 null 0.0 true null 0600-0659 null null null 1000-1059 true A false 180.0 null 1.0 1197.0 5 null null null null null null 2015-01-01T12:00:00.000+0000 2015-01-01T10:00:00.000+0000 72530094846 72202012839 2 KORD -6 America/Chicago 41.9786 -87.9048 672 KDEN -7 America/Denver 39.861698150635 -104.672996521 5431 2015 1 1 1 4 2015-01-01 UA null 1143 IL Chicago, IL 13930 ORD CO Denver, CO 11292 DEN 1627 null 0.0 true null 1600-1659 null null null 1800-1859 true B false 166.0 null 1.0 888.0 4 null null null null null null 2015-01-01T22:27:00.000+0000 2015-01-01T20:27:00.000+0000 72530094846 72565003017 3 KORD -6 America/Chicago 41.9786 -87.9048 672 KPHL -5 America/New_York 39.87189865112305 -75.24109649658203 36 2015 1 1 1 4 2015-01-01 UA null 1412 IL Chicago, IL 13930 ORD PA Philadelphia, PA 14100 PHL 1010 null 0.0 true null 1000-1059 null null null 1300-1359 true A false 121.0 null 1.0 678.0 3 null null null null null null 2015-01-01T16:10:00.000+0000 2015-01-01T14:10:00.000+0000 72530094846 72408013739 4 KORD -6 America/Chicago 41.9786 -87.9048 672 KEGE -7 America/Denver 39.64260101 -106.9179993 6548 2015 1 1 1 4 2015-01-01 AA N005AA 1080 IL Chicago, IL 13930 ORD CO Eagle, CO 11503 EGE 1145 null 0.0 true null 1100-1159 null null null 1300-1359 true A false 170.0 null 1.0 1007.0 5 null null null null null null 2015-01-01T17:45:00.000+0000 2015-01-01T15:45:00.000+0000 72530094846 72467523063 5 KATL -5 America/New_York 33.6367 -84.428101 1026 KDFW -6 America/Chicago 32.896801 -97.038002 607 2015 1 1 1 4 2015-01-01 AA N025AA 1635 GA Atlanta, GA 10397 ATL TX Dallas/Fort Worth, TX 11298 DFW 0625 null 0.0 true null 0600-0659 null null null 0700-0759 true B false 150.0 null 1.0 731.0 3 null null null null null null 2015-01-01T11:25:00.000+0000 2015-01-01T09:25:00.000+0000 72219013874 72259003927 6 KORD -6 America/Chicago 41.9786 -87.9048 672 KDFW -6 America/Chicago 32.896801 -97.038002 607 2015 1 1 1 4 2015-01-01 AA N4YFAA 2335 IL Chicago, IL 13930 ORD TX Dallas/Fort Worth, TX 11298 DFW 1450 null 0.0 true null 1400-1459 null null null 1700-1759 true B false 150.0 null 1.0 802.0 4 null null null null null null 2015-01-01T20:50:00.000+0000 2015-01-01T18:50:00.000+0000 72530094846 72259003927 7 KATL -5 America/New_York 33.6367 -84.428101 1026 KDFW -6 America/Chicago 32.896801 -97.038002 607 2015 1 1 1 4 2015-01-01 NK N618NK 144 GA Atlanta, GA 10397 ATL TX Dallas/Fort Worth, TX 11298 DFW 1124 null 0.0 true null 1100-1159 null null null 1200-1259 true B false 148.0 null 1.0 731.0 3 null null null null null null 2015-01-01T16:24:00.000+0000 2015-01-01T14:24:00.000+0000 72219013874 72259003927 8 KORD -6 America/Chicago 41.9786 -87.9048 672 KCID -6 America/Chicago 41.884700775146484 -91.71080017089844 869 2015 1 1 1 4 2015-01-01 MQ N633MQ 3172 IL Chicago, IL 13930 ORD IA Cedar Rapids/Iowa City, IA 11003 CID 1330 null 0.0 true null 1300-1359 null null null 1400-1459 true A false 68.0 null 1.0 196.0 1 null null null null null null 2015-01-01T19:30:00.000+0000 2015

We apply the join to the full data and write the intermediate table to parquet:

In [0]:
# read if necessary
df_airlines_full_clean = spark.read.parquet(f"{blob_url}/airlines_clean_full_v1/*")
df_stations_clean = spark.read.parquet(f"{blob_url}/stations_clean_full/*")

# join stations
df_airlines_stations_full = join_stations_to_airlines(df_airlines_full_clean, df_stations_clean)

# write
df_airlines_stations_full.write.mode('overwrite').parquet(f"{blob_url}/full_airlines_stations_v0")

#### Weather to Airport Join

The weather to airport join takes the station and airport dataset, the weather data, and the airport a prefix (either `origin_` or `dest_`). It first prepares the weather dataset by droping duplicates and prepending the column names with the specified the prefix. Next, the weather is joined to the airlines using the station ids and the prediction time, with a 2-hour buffer for the weather time. This time range join is because the weather data is rarely recorded at exact same time as a flight prediction time. This does cause duplicate flight measurements to be generated, when there are more than one weather measurement in the 2-hour window, so we need to address this. A new feature indicating the difference between the prediction time and weather recording time is generated (`weather_offset_minutes`). Finally, we are able to drop duplicate flight records by ordering our datset by index ID (chronological flights) and weather offset (increasing) and dropping on these keys. This results in flight records now having the closest weather measurement recorded within 2 hours of the prediction time. The function is shown below:

In [0]:
def join_weather_to_airlines(airlines, weather, prefix):
  # subset and rename
  weather = weather.dropDuplicates(subset=['STATION', 'DATE'])\
                   .select([col(c).alias(prefix+str.lower(c)) for c in weather.columns if c not in ['LATITUDE', 'LONGITUDE', 'NAME']])\
  
  # join weather by station id and prediction time with 2 hour buffer, sort and drop duplicates
  joined = airlines.alias('a').join(weather.alias('w'),
                                    (col(f"a.{prefix}station_id") == col(f"w.{prefix}station")) &\
                                    (col(f"w.{prefix}date").between(col("a.time_at_prediction_utc") + expr('INTERVAL -2 HOURS'),
                                                                    col("a.time_at_prediction_utc"))),
                                    'left')\
                              .select('a.*',
                                      'w.*',
                                      ((unix_timestamp(col(f"{prefix}date")) - unix_timestamp(col("a.time_at_prediction_utc")))/60).alias(f"{prefix}weather_offset_minutes"))\
                              .drop(f"{prefix}station", f"{prefix}date")\
                              .fillna(value=0, subset=[f"{prefix}weather_offset_minutes"])\
                              .orderBy(col("index_id").asc(),col(f"{prefix}weather_offset_minutes").desc())\
                              .dropDuplicates(['index_id'])
  
  return joined

We'll again first apply this join to our subset 3 month datasets:

In [0]:
# read if necessary
df_weather_clean = spark.read.parquet(f"{blob_url}/weather_eda_v0/*")
df_airlines_stations_clean = spark.read.parquet(f"{blob_url}/airlines_stations_v0/*")

# join origin weather
df_airlines_weather_origin = join_weather_to_airlines(df_airlines_stations_clean, df_weather_clean, "origin_")

# display
display(df_airlines_weather_origin.limit(10))

# write
df_airlines_weather_origin.write.mode('overwrite').parquet(f"{blob_url}/airlines_weather_origin_v0")

index_id origin_ICAO origin_utc_offset origin_timezone origin_latitude origin_longitude origin_altitude dest_ICAO dest_utc_offset dest_timezone dest_latitude dest_longitude dest_altitude year quarter month day_of_month day_of_week dt carrier tail_num flight_num origin_state origin_city origin_airport_id origin_airport_code dest_state dest_city dest_airport_id dest_airport_code planned_dep_time actual_dep_time delay_minutes dep_is_delayed dep_delay_group dep_hour actual_arr_time arr_delay_minutes arr_delay_group arr_hour canceled cancel_code is_diverted planned_duration actual_duration num_flights flight_distance distance_group carrier_delay weather_delay nas_delay security_delay late_aircraft_delay div_reached_dest planned_departure_utc time_at_prediction_utc origin_station_id dest_station_id origin_wnd_angle origin_wnd_angle_qc origin_wnd_type origin_wnd_speed origin_wnd_speed_qc origin_cig_cloud_agl origin_cig_cloud_agl_qc origin_cig_method origin_cig_cavok origin_vis_dist origin_vis_dist_qc origin_vis_var origin_vis_var_qc origin_tmp_c origin_tmp_qc origin_dew_c origin_dew_qc origin_slp_p origin_slp_qc origin_weather_offset_minutes 1 KORD -6 America/Chicago 41.9786 -87.9048 672 KMIA -5 America/New_York 25.79319953918457 -80.29060363769531 8 2015 1 1 1 4 2015-01-01 F9 null 1256 IL Chicago, IL 13930 ORD FL Miami, FL 13303 MIA 0600 null 0.0 true null 0600-0659 null null null 1000-1059 true A false 180.0 null 1.0 1197.0 5 null null null null null null 2015-01-01T12:00:00.000+0000 2015-01-01T10:00:00.000+0000 72530094846 72202012839 250 5 N 67 5 22000 5 9 N 16093 5 N 5 -94 5 -150 5 10190 5 -9.0 2 KORD -6 America/Chicago 41.9786 -87.9048 672 KDEN -7 America/Denver 39.861698150635 -104.672996521 5431 2015 1 1 1 4 2015-01-01 UA null 1143 IL Chicago, IL 13930 ORD CO Denver, CO 11292 DEN 1627 null 0.0 true null 1600-1659 null null null 1800-1859 true B false 166.0 null 1.0 888.0 4 null null null null null null 2015-01-01T22:27:00.000+0000 2015-01-01T20:27:00.000+0000 72530094846 72565003017 240 5 N 67 5 7620 5 M N 16093 5 N 5 -17 5 -106 5 10156 5 -36.0 3 KORD -6 America/Chicago 41.9786 -87.9048 672 KPHL -5 America/New_York 39.87189865112305 -75.24109649658203 36 2015 1 1 1 4 2015-01-01 UA null 1412 IL Chicago, IL 13930 ORD PA Philadelphia, PA 14100 PHL 1010 null 0.0 true null 1000-1059 null null null 1300-1359 true A false 121.0 null 1.0 678.0 3 null null null null null null 2015-01-01T16:10:00.000+0000 2015-01-01T14:10:00.000+0000 72530094846 72408013739 240 5 N 57 5 22000 5 9 N 16093 5 N 5 -94 5 -144 5 10186 5 -19.0 4 KORD -6 America/Chicago 41.9786 -87.9048 672 KEGE -7 America/Denver 39.64260101 -106.9179993 6548 2015 1 1 1 4 2015-01-01 AA N005AA 1080 IL Chicago, IL 13930 ORD CO Eagle, CO 11503 EGE 1145 null 0.0 true null 1100-1159 null null null 1300-1359 true A false 170.0 null 1.0 1007.0 5 null null null null null null 2015-01-01T17:45:00.000+0000 2015-01-01T15:45:00.000+0000 72530094846 72467523063 240 5 N 93 5 22000 5 9 N 16093 5 N 5 -83 5 -144 5 10187 5 -54.0 5 KATL -5 America/New_York 33.6367 -84.428101 1026 KDFW -6 America/Chicago 32.896801 -97.038002 607 2015 1 1 1 4 2015-01-01 AA N025AA 1635 GA Atlanta, GA 10397 ATL TX Dallas/Fort Worth, TX 11298 DFW 0625 null 0.0 true null 0600-0659 null null null 0700-0759 true B false 150.0 null 1.0 731.0 3 null null null null null null 2015-01-01T11:25:00.000+0000 2015-01-01T09:25:00.000+0000 72219013874 72259003927 999 9 C 0 5 22000 5 9 N 16093 5 N 5 17 5 -33 5 10274 5 -33.0 6 KORD -6 America/Chicago 41.9786 -87.9048 672 KDFW -6 America/Chicago 32.896801 -97.038002 607 2015 1 1 1 4 2015-01-01 AA N4YFAA 2335 IL Chicago, IL 13930 ORD TX Dallas/Fort Worth, TX 11298 DFW 1450 null 0.0 true null 1400-1459 null null null 1700-1759 true B false 150.0 null 1.0 802.0 4 null null null null null null 2015-01-01T20:50:00.000+0000 2015-01-01T18:50:00.000+0000 72530094846 72259003927 240 1 N 77 1 null 9 9 N 16000 1 9 9 -39 1 -122 1 10165 1 -50.0 7 KATL -5 America/New_York 33.6367 -84.428101 1026 K

While we were able to join the airlines and *stations* together in one go, the weather is significantly more computationally expensive. We opt to split the weather join into a separate join for each year, in order to reduce the risk of the full join being interrupted and needing to start over. Each year is written to parquet for safekeeping, with the next step being to union these datasets together for a comprehensive set. 

The code below does not show the duration of the commands, however, we recorded the time each join took to run. We were unable to note how many nodes the computation had access to due to fluctuations in availability during this time period.
- 2015 join: 1.69 hours
- 2016 join: 1.58 hours
- 2017 join: 1.47 hours
- 2018 join: 1.72 hours
- 2019 join: 1.59 hours

In [0]:
# read datasets if necessary
df_airlines_stations_full = spark.read.parquet(f"{blob_url}/full_airlines_stations_v0/*").cache()
df_weather_full_clean = spark.read.parquet(f"{blob_url}/weather_clean_full/*").cache()

# join
full_join_2015 = join_weather_to_airlines(df_airlines_stations_full.filter(col('time_at_prediction_utc') < "2016-01-01T00:00:00.000"),
                                          weather_clean_full_v1.filter(col('DATE') < "2016-01-01T00:00:00.000"),
                                          "origin_")


# write
full_join_2015.write.mode('overwrite').parquet(f"{blob_url}/full_join_2015_v0")

java.lang.RuntimeException: abort: DriverClient destroyed
	at com.databricks.backend.daemon.driver.DriverClient.$anonfun$poll$3(DriverClient.scala:410)
	at scala.concurrent.Future.$anonfun$flatMap$1(Future.scala:307)
	at scala.concurrent.impl.Promise.$anonfun$transformWith$1(Promise.scala:41)
	at scala.concurrent.impl.CallbackRunnable.run(Promise.scala:64)
	at com.databricks.threading.NamedExecutor$$anon$2.$anonfun$run$1(NamedExecutor.scala:356)
	at scala.runtime.java8.JFunction0$mcV$sp.apply(JFunction0$mcV$sp.java:23)
	at com.databricks.logging.UsageLogging.$anonfun$withAttributionContext$1(UsageLogging.scala:240)
	at scala.util.DynamicVariable.withValue(DynamicVariable.scala:62)
	at com.databricks.logging.UsageLogging.withAttributionContext(UsageLogging.scala:235)
	at com.databricks.logging.UsageLogging.withAttributionContext$(UsageLogging.scala:232)
	at com.databricks.threading.NamedExecutor.withAttributionContext(NamedExecutor.scala:285)
	at com.databricks.threading.NamedExecutor$$anon$2.run(NamedExecutor.scala:355)
	at java.base/java.util.concurrent.ThreadPoolExecutor.runWorker(ThreadPoolExecutor.java:1128)
	at java.base/java.util.concurrent.ThreadPoolExecutor$Worker.run(ThreadPoolExecutor.java:628)
	at java.base/java.lang.Thread.run(Thread.java:834)

In [0]:
# join 2016 weather and airports
full_join_2016 = join_weather_to_airlines(df_airlines_stations_full.filter((col('time_at_prediction_utc') >= "2016-01-01T00:00:00.000") &\
                                                               (col('time_at_prediction_utc') < "2017-01-01T00:00:00.000")),
                                          weather_clean_full_v1.filter((col('DATE') >= "2016-01-01T00:00:00.000") &\
                                                                       (col('DATE') < "2017-01-01T00:00:00.000")),
                                          "origin_")


# write
full_join_2016.write.mode('overwrite').parquet(f"{blob_url}/full_join_2016_v0")

In [0]:
# join 2017 weather and airports
full_join_2017 = join_weather_to_airlines(df_airlines_stations_full.filter((col('time_at_prediction_utc') >= "2017-01-01T00:00:00.000") &\
                                                               (col('time_at_prediction_utc') < "2018-01-01T00:00:00.000")),
                                          weather_clean_full_v1.filter((col('DATE') >= "2017-01-01T00:00:00.000") &\
                                                                       (col('DATE') < "2018-01-01T00:00:00.000")),
                                          "origin_")


# write
full_join_2017.write.mode('overwrite').parquet(f"{blob_url}/full_join_2017_v0")

In [0]:
# join 2018 weather and airports
full_join_2018 = join_weather_to_airlines(df_airlines_stations_full.filter((col('time_at_prediction_utc') >= "2018-01-01T00:00:00.000") &\
                                                               (col('time_at_prediction_utc') < "2019-01-01T00:00:00.000")),
                                          weather_clean_full_v1.filter((col('DATE') >= "2018-01-01T00:00:00.000") &\
                                                                       (col('DATE') < "2019-01-01T00:00:00.000")),
                                          "origin_")


# write
full_join_2018.write.mode('overwrite').parquet(f"{blob_url}/full_join_2018_v0")

In [0]:
# join 2019 weather and airports
full_join_2019 = join_weather_to_airlines(df_airlines_stations_full.filter((col('time_at_prediction_utc') >= "2019-01-01T00:00:00.000")),
                                          weather_clean_full_v1.filter((col('DATE') >= "2019-01-01T00:00:00.000")),
                                          "origin_")


# write
full_join_2019.write.mode('overwrite').parquet(f"{blob_url}/full_join_2019_v0")

In [0]:
# union all datasets
full_join  = spark.read.parquet(f"{blob_url}/full_join_2015_v0/*")\
             .union(spark.read.parquet(f"{blob_url}/full_join_2016_v0/*"))\
             .union(spark.read.parquet(f"{blob_url}/full_join_2017_v0/*"))\
             .union(spark.read.parquet(f"{blob_url}/full_join_2018_v0/*"))\
             .union(spark.read.parquet(f"{blob_url}/full_join_2019_v0/*")).cache()

# write
full_join.write.mode('overwrite').parquet(f"{blob_url}/full_join_2015_2019_v0")

In [0]:
display(full_join.limit(10))

index_id origin_ICAO origin_utc_offset origin_timezone origin_latitude origin_longitude origin_altitude dest_ICAO dest_utc_offset dest_timezone dest_latitude dest_longitude dest_altitude year quarter month day_of_month day_of_week dt carrier tail_num flight_num origin_state origin_city origin_airport_id origin_airport_code dest_state dest_city dest_airport_id dest_airport_code planned_dep_time actual_dep_time delay_minutes dep_is_delayed dep_delay_group dep_hour actual_arr_time arr_delay_minutes arr_delay_group arr_hour canceled cancel_code is_diverted planned_duration actual_duration num_flights flight_distance distance_group carrier_delay weather_delay nas_delay security_delay late_aircraft_delay div_reached_dest planned_departure_utc time_at_prediction_utc origin_station_id dest_station_id origin_wnd_angle origin_wnd_angle_qc origin_wnd_type origin_wnd_speed origin_wnd_speed_qc origin_cig_cloud_agl origin_cig_cloud_agl_qc origin_cig_method origin_cig_cavok origin_vis_dist origin_vis_dist_qc origin_vis_var origin_vis_var_qc origin_tmp_c origin_tmp_qc origin_dew_c origin_dew_qc origin_slp_p origin_slp_qc origin_weather_offset_minutes 3 KORD -6 America/Chicago 41.9786 -87.9048 672 KMIA -5 America/New_York 25.79319953918457 -80.29060363769531 8 2015 1 1 1 4 2015-01-01 F9 null 1256 IL Chicago, IL 13930 ORD FL Miami, FL 13303 MIA 0600 null 0.0 true null 0600-0659 null null null 1000-1059 true A false 180.0 null 1.0 1197.0 5 null null null null null null 2015-01-01T12:00:00.000+0000 2015-01-01T10:00:00.000+0000 72530094846 72202012839 250 5 N 67 5 22000 5 9 N 16093 5 N 5 -94 5 -150 5 10190 5 -9.0 142 KDFW -6 America/Chicago 32.896801 -97.038002 607 KEWR -5 America/New_York 40.692501068115234 -74.168701171875 18 2015 1 1 1 4 2015-01-01 AA N3BJAA 2488 TX Dallas/Fort Worth, TX 11298 DFW NJ Newark, NJ 11618 EWR 1130 null 0.0 true null 1100-1159 null null null 1500-1559 true B false 185.0 null 1.0 1372.0 6 null null null null null null 2015-01-01T17:30:00.000+0000 2015-01-01T15:30:00.000+0000 72259003927 72502014734 320 5 N 15 5 183 5 M N 3219 5 N 5 0 5 -11 5 null 9 -6.0 178 KDFW -6 America/Chicago 32.896801 -97.038002 607 KSFO -8 America/Los_Angeles 37.61899948120117 -122.375 13 2015 1 1 1 4 2015-01-01 AA N3LCAA 184 TX Dallas/Fort Worth, TX 11298 DFW CA San Francisco, CA 14771 SFO 1025 null 0.0 true null 1000-1059 null null null 1200-1259 true B false 225.0 null 1.0 1464.0 6 null null null null null null 2015-01-01T16:25:00.000+0000 2015-01-01T14:25:00.000+0000 72259003927 72494023234 020 5 N 15 5 762 5 M N 3219 5 N 5 0 5 -17 5 null 9 -5.0 308 KAMA -6 America/Chicago 35.219398 -101.706001 3607 KDFW -6 America/Chicago 32.896801 -97.038002 607 2015 1 1 1 4 2015-01-01 MQ N518MQ 3414 TX Amarillo, TX 10279 AMA TX Dallas/Fort Worth, TX 11298 DFW 1310 null 0.0 true null 1300-1359 null null null 1400-1459 true A false 75.0 null 1.0 312.0 2 null null null null null null 2015-01-01T19:10:00.000+0000 2015-01-01T17:10:00.000+0000 72363023047 72259003927 230 5 N 36 5 122 5 M N 3219 5 N 5 -56 5 -67 5 10239 5 -17.0 328 KDFW -6 America/Chicago 32.896801 -97.038002 607 KMAF -6 America/Chicago 31.9424991607666 -102.2020034790039 2871 2015 1 1 1 4 2015-01-01 MQ N543MQ 2791 TX Dallas/Fort Worth, TX 11298 DFW TX Midland/Odessa, TX 13158 MAF 2130 null 0.0 true null 2100-2159 null null null 2200-2259 true B false 68.0 null 1.0 309.0 2 null null null null null null 2015-01-02T03:30:00.000+0000 2015-01-02T01:30:00.000+0000 72259003927 72265023023 020 5 N 31 5 488 5 M N 9656 5 N 5 17 5 6 5 null 9 -18.0 867 KDEN -7 America/Denver 39.861698150635 -104.672996521 5431 KMOT -6 America/Chicago 48.2593994140625 -101.27999877929688 1716 2015 1 1 1 4 2015-01-01 OO N932EV 5563 CO Denver, CO 11292 DEN ND Minot, ND 13433 MOT 1945 null 0.0 true null 1900-1959 null null null 2200-2259 true C false 115.0 null 1.0 604.0 3 null null null null null null 2015-01-02T02:45:00.000+0000 2015-01-02T00:45:00.000+0000 72565003017 72767624013 210 5 N 31 5 366 5 M N 2012 5 N 5 -67 5 -83 

## Section 3 - Feature Engineering

#### Aggregate Features

In [0]:
def aggregate_keys(df, keys, name, count_only=False):
  if count_only:
    return df.groupBy(keys).agg(count('index_id').alias(f"n_flights_{name}"))
  
  else:
    return df.groupBy(keys).agg(count('index_id').alias(f"n_flights_{name}"),\
                                count(when(col("dep_is_delayed"), col("dep_is_delayed"))).alias(f"n_delayed_{name}"),\
                                (count(when(col("dep_is_delayed"), col("dep_is_delayed")))/count('dep_is_delayed') * 100).alias(f"pct_delayed_{name}"),\
                                mean('delay_minutes').alias(f"mean_delay_{name}"))

First we'll generate aggregates for the flight routes and origin/destinations:

In [0]:
full_join  = spark.read.parquet(f"{blob_url}/full_join_2015_2019_v0/*").cache()

# origin aggregates
agg_origin = aggregate_keys(full_join,
                            ['origin_ICAO'],
                            'from_origin')

# dest aggregates
agg_dest = aggregate_keys(full_join,
                          ['dest_ICAO'],
                          'to_dest')

# route (origin + destination) aggregates
agg_route = aggregate_keys(full_join,
                           ['origin_ICAO',
                           'dest_ICAO',
                           'origin_longitude',
                           'origin_latitude',
                           'dest_longitude',
                           'dest_latitude'],
                           'for_route')

# origin state aggregates
agg_origin_state = aggregate_keys(full_join,
                           ['origin_state'],
                           'from_state')

# dest state aggregates
agg_dest_state = aggregate_keys(full_join,
                         ['dest_state'],
                         'to_state')


Next, we'll join these features back onto the dataset:

In [0]:
def join_aggs(df, origin, dest, route, o_state, d_state):
  joined = df.alias('d').join(origin.alias('o'),
                              (col("d.origin_ICAO") == col("o.origin_ICAO")),
                              'left')\
                        .join(dest.alias('de'),
                              (col("d.dest_ICAO") == col("de.dest_ICAO")),
                              'left')\
                        .join(route.alias('r'),
                              (col("d.origin_ICAO") == col("r.origin_ICAO")) &\
                              (col("d.dest_ICAO") == col("r.dest_ICAO")),
                              'left')\
                        .join(o_state.alias('os'),
                              (col("d.origin_state") == col("os.origin_state")),
                              'left')\
                        .join(d_state.alias('ds'),
                              (col("d.dest_state") == col("ds.dest_state")),
                              'left')\
                        .select('d.*',
                                'o.pct_delayed_from_origin',
                                'o.mean_delay_from_origin',
                                'de.pct_delayed_to_dest',
                                'de.mean_delay_to_dest',
                                'r.pct_delayed_for_route',
                                'r.mean_delay_for_route',
                                'os.pct_delayed_from_state',
                                'os.mean_delay_from_state',
                                'ds.pct_delayed_to_state',
                                'ds.mean_delay_to_state'
                                )\
                        .orderBy(col("index_id").asc())
  return joined

In [0]:
# join
full_join_with_aggs = join_aggs(full_join, agg_origin, agg_dest, agg_route, agg_origin_state, agg_dest_state)

# write
full_join_with_aggs.write.mode('overwrite').parquet(f"{blob_url}/full_join_with_aggs_v0")

### Window Calculations

1. Previous Flight Delay (prev_fl_del)
  - Prior flight performance can have an impact on flight departure times. We tracked flights by their tail numbers and arrival times in order to determine if the previous flight was delayed. If the previous flight was delayed, we set the indicator to 1 and if it was not delayed, we set the indicator to 0. 
 
2. Potential for Delay (poten_for_del)
  - Previous flight arrival times can also have an impact on flight departure times. After landing, the plane needs to be refueled, cleaned, and maintenanced. The cabin crew and pilots may need to be changed. The more time in between the flight’s arrival time and next departure time, the less likely the flight departure will be delayed. We calculated the time in between flights by tracking the tail number and actual arrival time and created an indicator where flights with more than 2 hours in between flights were indicated with a 1 and less than 2 hours were indicated with a 0. Flights that were canceled, diverted, or did not have a previous flight were null and were indicated with a -1. 
 
3. Indicators for Average Delay 2-4 Hours Prior to Planned Departure 
  - At times, there may be certain issues, such as security, weather, maintenance, etc., that can affect flight performance at the airport or carrier level. We created a few indicator variables to capture the average delay minutes 2-4 hours prior to planned departure times. If the average delay 2-4 hours prior is less than 15 minutes, it is assigned a 0, and if it is greater than 15 minutes, it is assigned a 1. There are null values if there are no flights in the 2-4 hour measurement window. We assign nulls a -1. 

    - Origin Airport Average Delay 2-4 Hours Prior (oa_del_ind)
      - This feature is created based on calculating the average delay minutes 2-4 before planned departure at the origin airport. 

    - Destination Airport Average Delay 2-4 Hours Prior (da_del_ind)
      - For this feature, we are determining average arrival delay at the departure 2-4 hours prior to the departure time at the origin airport. The concept is similar to the previous feature. If there is an issue that is affecting the destination airport, then flights to that airport may be delayed. 

    - Carrier Average Delay 2-4 Hours Prior by Origin Airport (carrier_del_ind)
      - If a specific airline is low on maintenance or cleaning staff on a certain day, it may impact departure times. We created this feature by calculating the average delay minutes by carrier at the origin airport. 

    - Five Delay Categories Average Delay 2-4 Hours Prior by Origin Airport (security_window_del_ind, nas_window_del_ind, carrier_window_del_ind, weather_window_del_ind, late_ac_window_del_ind)
      - There were five features, security, NAS, carrier, weather, and late aircraft delay, that provided the total delay minutes for the specific category. We created five features to capture the average delay minutes of each category by origin airport

In [0]:
import pyspark.sql.functions as f
from pyspark.sql.window import Window

# access data
data = spark.read.parquet(f"{blob_url}/full_join_with_aggs_v0/*").cache()

# ensure data is in appropriate type
data = data.withColumn("dep_is_delayed",data["dep_is_delayed"].cast(IntegerType()))\
          .withColumn("security_delay",data["security_delay"].cast(IntegerType()))\
          .withColumn("is_diverted",data["is_diverted"].cast(IntegerType()))\
          .withColumn("delay_minutes",data["delay_minutes"].cast(IntegerType()))\
          .withColumn("arr_delay_minutes",data["arr_delay_minutes"].cast(IntegerType()))\
          .withColumn("carrier_delay",data["carrier_delay"].cast(IntegerType()))\
          .withColumn("weather_delay",data["weather_delay"].cast(IntegerType()))\
          .withColumn("nas_delay",data["nas_delay"].cast(IntegerType()))

####################################### New feature 1: potential for delay  ######################################
####################################### New feature 2: prev flight delay ind  ####################################
#Potential for delay: if flight arrives > 2 hrs before departure likelihood for delay is smaller
# pad if length is not equal to 4 
data = data.withColumn('actual_arr_time_pad', f.lpad(data['actual_arr_time'], 4, '0'))\
            .withColumn('actual_dep_time_pad', f.lpad(data['actual_dep_time'], 4, '0'))

# Convert actual arrival time and actual departure time to utc 
data = data.withColumn('actual_arr_utc', to_utc_timestamp(to_timestamp(concat(col('dt'), col('actual_arr_time_pad')), 'yyyy-MM-ddHHmm'), col('dest_timezone')))\
            .withColumn('actual_dep_utc', to_utc_timestamp(to_timestamp(concat(col('dt'), col('actual_dep_time_pad')), 'yyyy-MM-ddHHmm'), col('origin_timezone')))

# update rows where actual arrival date is greater than departure date 
data = data.withColumn("actual_arr_utc", f.when((data.actual_arr_utc < data.actual_dep_utc),(f.from_unixtime(f.unix_timestamp('actual_dep_utc') + (data.actual_duration*60)))).otherwise(data.actual_arr_utc))

# Group by tail number then sort by actual arrival time 
win_ind = Window.partitionBy('tail_num').orderBy('actual_arr_utc')
# Get the prior actual arrival time of each flight
# Calculate the hours in between prior actual arrival time and planned departure time 
# Categorize flight gap (>2 hours = 0, between 0-1 = 1, <0 = 2, and null = -1)
data = data.withColumn('prev_actual_arr_utc', f.lag('actual_arr_utc',1, None).over(win_ind))\
             .withColumn('prev_fl_del', f.lag('dep_is_delayed',1, None).over(win_ind))\
            .withColumn('inbtwn_fl_hrs', (f.unix_timestamp('planned_departure_utc') - f.unix_timestamp('prev_actual_arr_utc'))/60/60)\
            .withColumn('poten_for_del', expr("CASE WHEN inbtwn_fl_hrs < 2 THEN '0'" + "WHEN inbtwn_fl_hrs IS NULL THEN '-1'" + "ELSE '1' END"))


###################### New feature 3: Origin aiport avg dep delay 2-4 hrs prior to planned dept   #######################
# if there are serious weather issues or some "global" or "local" issue is occuring, then all flights should be delayed 

# Group by origin airport then sort by planned departure time to get avg dep delay by origin airport 2-4 hours before planned departure
win_ind_airport = Window.partitionBy('origin_airport_code')\
                         .orderBy(f.unix_timestamp('planned_departure_utc'))\
                         .rangeBetween(-14400, -7200)
data = data.withColumn('oa_avg_del2_4hr', f.round(f.avg('delay_minutes').over(win_ind_airport),2))\
            .withColumn('oa_avg_del_ind', expr("CASE WHEN oa_avg_del2_4hr < 15 THEN '0'" + "WHEN oa_avg_del2_4hr IS NULL THEN '-1'" + "ELSE '1' END"))


############### New feature 4: Carrier avg dep delay by origin airport 2-4 hrs prior to planned dept   ################# 
# Group by origin airport then sort by planned departure time to get avg dep delay by carrier 2-4 hours before planned departure at origin airport 
win_ind_carrier = Window.partitionBy([col('origin_airport_code'), col('carrier')])\
                         .orderBy(f.unix_timestamp('planned_departure_utc'))\
                         .rangeBetween(-14400, -7200)
data = data.withColumn('carrier_avg_del2_4hr', f.round(f.avg('delay_minutes').over(win_ind_carrier),2))\
            .withColumn('carrier_avg_del_ind', expr("CASE WHEN carrier_avg_del2_4hr < 15 THEN '0'" + "WHEN carrier_avg_del2_4hr IS NULL THEN '-1'" + "ELSE '1' END"))


############### New feature 5: Destination avg arrival delay by 2-4 hrs prior to planned dept   ################# 
# Group by destination airport then sort by planned departure time to get avg arr delay at dest airport 2-4 hours before planned departure  
win_ind_dest_airport = Window.partitionBy('dest_airport_code')\
                         .orderBy(f.unix_timestamp('planned_departure_utc'))\
                         .rangeBetween(-14400, -7200)
data = data.withColumn('da_avg_del2_4hr', f.round(f.avg('arr_delay_minutes').over(win_ind_dest_airport),2))\
            .withColumn('da_avg_del_ind', expr("CASE WHEN da_avg_del2_4hr < 15 THEN '0'" + "WHEN da_avg_del2_4hr IS NULL THEN '-1'" + "ELSE '1' END"))


############### New feature 6: Avg delay of 5 delay categories 2-4 hrs prior to planned dept   ################# 
# Unable to use delay categories, so determine the avg delay for each category 2-4 hours prior to planned departure at origin ariport   
win_ind_del = Window.partitionBy('origin_airport_code')\
                         .orderBy(f.unix_timestamp('planned_departure_utc'))\
                         .rangeBetween(-14400, -7200)
data = data.withColumn('weather_window_del', f.round(f.avg('weather_delay').over(win_ind_del),2))\
           .withColumn('carrier_window_del', f.round(f.avg('carrier_delay').over(win_ind_del),2))\
           .withColumn('security_window_del', f.round(f.avg('security_delay').over(win_ind_del),2))\
           .withColumn('late_ac_window_del', f.round(f.avg('late_aircraft_delay').over(win_ind_del),2))\
           .withColumn('nas_window_del', f.round(f.avg('nas_delay').over(win_ind_del),2))\
           .withColumn('weather_window_del_ind', expr("CASE WHEN weather_window_del < 15 THEN '0'" + "WHEN weather_window_del IS NULL THEN '-1'" + "ELSE '1' END"))\
           .withColumn('carrier_window_del_ind', expr("CASE WHEN carrier_window_del < 15 THEN '0'" + "WHEN carrier_window_del IS NULL THEN '-1'" + "ELSE '1' END"))\
           .withColumn('security_window_del_ind', expr("CASE WHEN security_window_del < 15 THEN '0'" + "WHEN security_window_del IS NULL THEN '-1'" + "ELSE '1' END"))\
           .withColumn('late_ac_window_del_ind', expr("CASE WHEN late_ac_window_del < 15 THEN '0'" + "WHEN late_ac_window_del IS NULL THEN '-1'" + "ELSE '1' END"))\
           .withColumn('nas_window_del_ind', expr("CASE WHEN nas_window_del < 15 THEN '0'" + "WHEN nas_window_del IS NULL THEN '-1'" + "ELSE '1' END"))

data.write.mode('overwrite').parquet(f"{blob_url}/full_join_with_windows_v0")

origin_ICAO origin_utc_offset origin_timezone origin_latitude origin_longitude origin_altitude dest_ICAO dest_utc_offset dest_timezone dest_latitude dest_longitude dest_altitude year quarter month day_of_month day_of_week dt carrier tail_num flight_num origin_state origin_city origin_airport_id origin_airport_code dest_state dest_city dest_airport_id dest_airport_code planned_dep_time actual_dep_time delay_minutes dep_is_delayed dep_delay_group dep_hour actual_arr_time arr_delay_minutes arr_delay_group arr_hour canceled cancel_code is_diverted planned_duration actual_duration num_flights flight_distance distance_group carrier_delay weather_delay nas_delay security_delay late_aircraft_delay div_reached_dest planned_departure_utc time_at_prediction_utc origin_station_id dest_station_id origin_wnd_angle origin_wnd_angle_qc origin_wnd_type origin_wnd_speed origin_wnd_speed_qc origin_cig_cloud_agl origin_cig_cloud_agl_qc origin_cig_method origin_cig_cavok origin_vis_dist origin_vis_dist_qc origin_vis_var origin_vis_var_qc origin_tmp_c origin_tmp_qc origin_dew_c origin_dew_qc origin_slp_p origin_slp_qc origin_weather_offset_minutes pct_delayed_from_origin mean_delay_from_origin pct_delayed_to_dest mean_delay_to_dest pct_delayed_for_route mean_delay_for_route pct_delayed_from_state mean_delay_from_state pct_delayed_to_state mean_delay_to_state index_id actual_arr_time_pad actual_dep_time_pad actual_arr_utc actual_dep_utc prev_actual_arr_utc prev_fl_del inbtwn_fl_hrs poten_for_del oa_avg_del2_4hr oa_avg_del_ind carrier_avg_del2_4hr carrier_avg_del_ind KBGM -5 America/New_York 42.20869827 -75.97979736 1636 KDTW -5 America/New_York 42.212398529052734 -83.35340118408203 645 2015 1 2 2 1 2015-02-02 EV N924EV 5400 NY Binghamton, NY 10577 BGM MI Detroit, MI 11433 DTW 0610 null 0 null null 0600-0659 null null null 0800-0859 null B null 112 null 1 378 2 null null null null null null 2015-02-02T11:10:00.000+0000 2015-02-02T09:10:00.000+0000 72515004725 72537094847 110 5 N 57 5 274 1 W N 1207 5 N 5 -44 1 -56 1 10016 1 -17 15 11 16 8 15 11 22 12 16 9 484144 null null null null null null null 1 null 1 null 1 KBGM -5 America/New_York 42.20869827 -75.97979736 1636 KDTW -5 America/New_York 42.212398529052734 -83.35340118408203 645 2015 1 2 2 1 2015-02-02 EV N933EV 5356 NY Binghamton, NY 10577 BGM MI Detroit, MI 11433 DTW 1715 1955 160 null 10 1700-1759 2156 185 12 1800-1859 null null null 96 121 1 378 2 26 0 25 0 134 null 2015-02-02T22:15:00.000+0000 2015-02-02T20:15:00.000+0000 72515004725 72537094847 320 5 N 103 5 610 5 M N 4023 5 N 5 -122 5 -156 5 null 9 -11 15 11 16 8 15 11 22 12 16 9 495350 2156 1955 2015-02-03 02:56:00 2015-02-03T00:55:00.000+0000 2015-02-03 00:28:00 null -2.216666666666667 1 null 1 null 1 KBGM -5 America/New_York 42.20869827 -75.97979736 1636 KDTW -5 America/New_York 42.212398529052734 -83.35340118408203 645 2015 1 2 3 2 2015-02-03 EV N933EV 5400 NY Binghamton, NY 10577 BGM MI Detroit, MI 11433 DTW 0610 618 8 null 0 0600-0659 804 2 0 0800-0859 null null null 112 106 1 378 2 null null null null null null 2015-02-03T11:10:00.000+0000 2015-02-03T09:10:00.000+0000 72515004725 72537094847 300 5 N 46 5 22000 5 9 N 11265 5 N 5 -150 5 -172 5 10188 5 -17 15 11 16 8 15 11 22 12 16 9 500095 0804 0618 2015-02-03 13:04:00 2015-02-03T11:18:00.000+0000 2015-02-03 04:55:00 null 6.25 0 null 1 null 1 KBGM -5 America/New_York 42.20869827 -75.97979736 1636 KDTW -5 America/New_York 42.212398529052734 -83.35340118408203 645 2015 1 2 3 2 2015-02-03 EV N933EV 5356 NY Binghamton, NY 10577 BGM MI Detroit, MI 11433 DTW 1715 1720 5 null 0 1700-1759 1859 8 0 1800-1859 null null null 96 99 1 378 2 null null null null null null 2015-02-03T22:15:00.000+0000 2015-02-03T20:15:00.000+0000 72515004725 72537094847 260 5 N 62 5 22000 5 9 N 16093 5 N 5 -78 5 -161 5 10216 5 -22 15 11 16 8 15 11 22 12 16 9 510824 1859 1720 2015-02-03 23:59:00 2015-02-03T22:20:00.000+0000 2015-02-03 21:51:00 null 0.4 1 null 1 null 1 KBGM -5 America/New_York 42.20869827 -75.97979736 1

### Holiday and Holiday-Adjacent
Airports typically see the most traffic during the holiday seasons. We captured this information by setting flights that depart on a US holiday to a  “holiday” category. We also set the two days prior and after a holiday to “holiday_adjacent” category since many people travel to a location before the actual holiday, spend time with their family or friends, and then fly back home after the holiday.

In [0]:
data = spark.read.parquet(f"{blob_url}/full_join_with_windows_v0/*").cache()
data = data.withColumn('holiday', expr("""CASE WHEN dt in ('2015-12-25', '2016-12-25', '2017-12-25', '2018-12-25', '2019-12-25',
                                                         '2015-11-26', '2016-11-24', '2017-11-23', '2018-11-22', '2019-11-28', 
                                                         '2015-01-01', '2016-01-01', '2017-01-01', '2018-01-01', '2019-01-01', 
                                                         '2015-01-01', '2016-01-01', '2017-01-01', '2018-01-01', '2019-01-01', 
                                                         '2015-07-04', '2016-07-04', '2017-07-04', '2018-07-04', '2019-07-04') THEN 'holiday' """ + 
                                                         """ WHEN dt in ('2015-12-23', '2015-12-24', '2015-12-26', '2015-12-27', '2016-12-23', 
                                                                    '2016-12-24', '2016-12-26', '2016-12-27', '2017-12-23', '2017-12-24', 
                                                                    '2017-12-26', '2017-12-27', '2018-12-23', '2018-12-24', '2018-12-26', 
                                                                    '2018-12-27', '2019-12-23', '2019-12-24', '2019-12-26', '2019-12-27', 
                                                                    '2015-11-24', '2015-11-25', '2015-11-27', '2015-11-28', '2016-11-22', 
                                                                    '2016-11-24', '2016-11-25', '2016-11-26', '2017-11-21', '2017-11-22', 
                                                                    '2017-11-24', '2017-11-25', '2018-11-20', '2018-11-21', '2018-11-23', 
                                                                    '2018-11-24', '2019-11-26', '2019-11-27', '2019-11-29', '2019-11-30', 
                                                                    '2015-01-02', '2015-01-03', '2015-12-30', '2015-12-31', '2016-01-02', 
                                                                    '2016-01-03', '2016-12-30', '2016-12-31', '2017-01-02', '2017-01-03', 
                                                                    '2017-12-30', '2017-12-31', '2018-01-02', '2018-01-03', '2018-12-30', 
                                                                    '2018-12-31', '2019-01-02', '2019-01-03', '2019-12-30', '2019-12-31', 
                                                                    '2015-07-02', '2015-07-03', '2015-07-05', '2015-07-06', '2016-07-02', 
                                                                    '2016-07-03', '2016-07-05', '2016-07-06', '2017-07-02', '2017-07-03', 
                                                                    '2017-07-05', '2017-07-06', '2018-07-02', '2018-07-03', '2018-07-05', 
                                                                    '2018-07-06', '2019-07-02', '2019-07-03', '2019-07-05', '2019-07-06') THEN 'holiday_adjacent' """
                                      "ELSE 'non-holiday' END"))

data.write.mode('overwrite').parquet(f"{blob_url}/full_join_with_holidays_v0")

### Mean Imputation and Null removal
List of features to fill

In [0]:
features_with_numeric_nulls = [
  'origin_wnd_speed',
  'origin_cig_cloud_agl',
  'origin_vis_dist',
  'origin_tmp_c',
  'origin_dew_c',
  'origin_slp_p'
]

features_with_str_nulls = [
  'origin_wnd_type',
  'origin_cig_cavok',
  'origin_vis_var'
]

This function will fill categorical nulls with the word "NULL" and numeric nulls with the mean of the feature:

In [0]:
def fill_nulls(data, features_with_numeric_nulls, features_with_str_nulls):
  # indicate numeric nulls
  data = data.select(["*"] + [col(x).isNull().cast(StringType()).alias(f"{x}_null") for x in features_with_numeric_nulls]).cache()
  
  for col_name in features_with_numeric_nulls:   
    # calculate mean for column after dropping nulls
    col_mean = data.select(col(col_name)).na.drop().select(mean(col(col_name)).alias('mean')).collect()[0]['mean']

    # replace nulls with mean
    data = data.withColumn(col_name, when(col(col_name).isNull(), col_mean).otherwise(col(col_name)))

  for col_name in features_with_str_nulls:
    # replace nulls with str
    data = data.withColumn(col_name, when(col(col_name).isNull(), 'NULL').otherwise(col(col_name)))
  
  return data

In [0]:
full_join_with_holidays = spark.read.parquet(f"{blob_url}/full_join_with_holidays_v0/*").cache()
feature_complete = fill_nulls(full_join_with_holidays,
                             features_with_numeric_nulls,
                             features_with_str_nulls)

feature_complete.write.mode('overwrite').parquet(f"{blob_url}/feature_complete_v6")

### Feature Selection
Let's subset down to only the features we will use in our predictive models:

In [0]:
model_features = [
  'dep_is_delayed', # outcome
  'canceled',       # outcome classification
  'planned_departure_utc', # datetime for cross validation
  'origin_state', # origin features
  'origin_city',
  'origin_ICAO',
  'origin_altitude',
  'origin_wnd_type', # origin weather
  'origin_wnd_speed',
  'origin_cig_cloud_agl',
  'origin_cig_cavok',
  'origin_vis_dist',
  'origin_vis_var',
  'origin_tmp_c',
  'origin_dew_c',
  'origin_slp_p',
  'dest_state', # dest features
  'dest_city',
  'dest_ICAO',
  'dest_altitude',
  'carrier', # flight features
  'year',
  'quarter',
  'month',
  'day_of_month',
  'day_of_week',
  'dep_hour',
  'arr_hour',
  'planned_duration',
  'flight_distance',
  'distance_group',
  'pct_delayed_from_origin', # aggregates
  'mean_delay_from_origin',
  'pct_delayed_to_dest',
  'mean_delay_to_dest',
  'pct_delayed_for_route',
  'mean_delay_for_route',
  'pct_delayed_from_state',
  'mean_delay_from_state',
  'pct_delayed_to_state',
  'mean_delay_to_state',
  'oa_avg_del_ind',
  'da_avg_del_ind',
  'carrier_avg_del_ind',
  'poten_for_del',
  'prev_fl_del',
  'nas_window_del_ind',
  'weather_window_del_ind',
  'carrier_window_del_ind',
  'security_window_del_ind',
  'late_ac_window_del_ind',
  'holiday'
] + [f"{x}_null" for x in features_with_numeric_nulls]


# final.write.mode('overwrite').parquet(f"{blob_url}/feature_complete_v6")
model_data = final.select(model_features).dropna(how='any').write.mode('overwrite').parquet(f"{blob_url}/model_features_v6")

For these features, we will print any remaining nulls

In [0]:
from pyspark.sql.functions import isnan, when, count, col
display(model_data)
display(model_data.select([count(when(isnan(c) | col(c).isNull(), c)).alias(c) for c in model_data.columns if c != "planned_departure_utc"]))
print(model_data.count())

dep_is_delayed canceled planned_departure_utc origin_state origin_city origin_ICAO origin_altitude origin_wnd_type origin_wnd_speed origin_cig_cloud_agl origin_cig_cavok origin_vis_dist origin_vis_var origin_tmp_c origin_dew_c origin_slp_p dest_state dest_city dest_ICAO dest_altitude carrier year quarter month day_of_month day_of_week dep_hour arr_hour planned_duration flight_distance distance_group pct_delayed_from_origin mean_delay_from_origin pct_delayed_to_dest mean_delay_to_dest pct_delayed_for_route mean_delay_for_route pct_delayed_from_state mean_delay_from_state pct_delayed_to_state mean_delay_to_state holiday origin_wnd_type_null origin_wnd_speed_null origin_cig_cloud_agl_null origin_cig_cavok_null origin_vis_dist_null origin_vis_var_null origin_tmp_c_null origin_dew_c_null origin_slp_p_null false false 2015-01-01T09:05:00.000+0000 AK Anchorage, AK PANC 152.0 N 21.0 1280.0 N 16093.0 N 28.0 6.0 10233.0 WA Seattle, WA KSEA 433.0 AS 2015 1 1 1 4 0001-0559 0001-0559 205.0 1448.0 6 9.83520120261614 0.8724688407992013 16.43483964019575 6.145191876804734 8.093694755450795 -0.2997053624042428 11.030319219981301 -0.4834406304260719 16.565504696142852 6.286257882148293 holiday false false false false false false false false false false false 2015-01-01T08:10:00.000+0000 CA Los Angeles, CA KLAX 125.0 C 0.0 12479.802773912874 N 16000.0 9 83.0 -100.0 10179.0 FL West Palm Beach/Palm Beach, FL KPBI 19.0 AA 2015 1 1 1 4 0001-0559 0700-0759 280.0 2330.0 10 21.486811350091894 10.485671790061964 22.715890333749343 11.854789491058705 11.688311688311687 4.883116883116883 20.23576491502932 9.533154260269752 20.265895898289283 10.53228037685095 holiday false false true false false false false false false false false 2015-01-01T08:20:00.000+0000 CA San Francisco, CA KSFO 13.0 N 21.0 12479.802773912874 N 16000.0 9 72.0 22.0 10187.0 NC Charlotte, NC KCLT 748.0 US 2015 1 1 1 4 0001-0559 0800-0859 286.0 2296.0 10 22.89276976963177 12.019219939855176 16.557974220386658 7.017735308741668 14.196020006385016 5.30190486325423 20.23576491502932 9.533154260269752 17.903528650048557 7.991099841105581 holiday false false true false false false false false false false false 2015-01-01T08:20:00.000+0000 CA Los Angeles, CA KLAX 125.0 C 0.0 12479.802773912874 N 16000.0 9 83.0 -100.0 10179.0 FL Miami, FL KMIA 8.0 AA 2015 1 1 1 4 0001-0559 0800-0859 285.0 2342.0 10 21.486811350091894 10.485671790061964 18.227905879456777 9.81727475074878 19.868711815936564 11.82958533731964 20.23576491502932 9.533154260269752 20.265895898289283 10.53228037685095 holiday false false true false false false false false false false false 2015-01-01T08:25:00.000+0000 CA San Francisco, CA KSFO 13.0 N 21.0 12479.802773912874 N 16000.0 9 72.0 22.0 10187.0 MN Minneapolis, MN KMSP 841.0 DL 2015 1 1 1 4 0001-0559 0600-0659 217.0 1589.0 7 22.89276976963177 12.019219939855176 15.40571797423415 8.17815405516324 16.210965606562095 7.277593898402648 20.23576491502932 9.533154260269752 15.51499295740704 8.257378442592778 holiday false false true false false false false false false false false 2015-01-01T08:25:00.000+0000 WA Seattle, WA KSEA 433.0 N 36.0 12479.802773912874 N 16000.0 9 6.0 -61.0 10314.0 AK Anchorage, AK PANC 152.0 AS 2015 1 1 1 4 0001-0559 0001-0559 235.0 1448.0 6 16.129214141680922 6.7084862252596995 14.335887970017616 2.759007619026246 14.964186059891263 5.063026781347985 15.786905806766386 6.527221454727693 13.057996954558812 1.1261774370208104 holiday false false true false false false false false false false false 2015-01-01T08:25:00.000+0000 NV Las Vegas, NV KLAS 2181.0 N 21.0 12479.802773912874 N 16000.0 9 22.0 -78.0 10159.0 MN Minneapolis, MN KMSP 841.0 NK 2015 1 1 1 4 0001-0559 0001-0559 181.0 1299.0 6 21.159724233522283 10.24774633828458 15.40571797423415 8.17815405516324 13.181623014169173 5.980034349506226 20.78637163855175 10.025912376463575 15.51499295740704 8.257378442592778 holiday false false true false false false false false false false false 2015-01-01T08:30:

dep_is_delayed canceled origin_state origin_city origin_ICAO origin_altitude origin_wnd_type origin_wnd_speed origin_cig_cloud_agl origin_cig_cavok origin_vis_dist origin_vis_var origin_tmp_c origin_dew_c origin_slp_p dest_state dest_city dest_ICAO dest_altitude carrier year quarter month day_of_month day_of_week dep_hour arr_hour planned_duration flight_distance distance_group pct_delayed_from_origin mean_delay_from_origin pct_delayed_to_dest mean_delay_to_dest pct_delayed_for_route mean_delay_for_route pct_delayed_from_state mean_delay_from_state pct_delayed_to_state mean_delay_to_state holiday origin_wnd_type_null origin_wnd_speed_null origin_cig_cloud_agl_null origin_cig_cavok_null origin_vis_dist_null origin_vis_var_null origin_tmp_c_null origin_dew_c_null origin_slp_p_null 4744 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1458 1458 0 0 0 0 0 0 0 0 164 0 0 0 0 1458 1458 1458 1458 0 0 0 0 0 0 0 0 0 0 0 0 0 0

31745270

There appear to be nulls in the `dep_is_delayed` outcome variable. Let's take a look:

In [0]:
display(model_data.filter(col('dep_is_delayed').isNull()))

origin_ICAO origin_utc_offset origin_timezone origin_latitude origin_longitude origin_altitude dest_ICAO dest_utc_offset dest_timezone dest_latitude dest_longitude dest_altitude year quarter month day_of_month day_of_week dt carrier tail_num flight_num origin_state origin_city origin_airport_id origin_airport_code dest_state dest_city dest_airport_id dest_airport_code planned_dep_time actual_dep_time delay_minutes dep_is_delayed dep_delay_group dep_hour actual_arr_time arr_delay_minutes arr_delay_group arr_hour canceled cancel_code is_diverted planned_duration actual_duration num_flights flight_distance distance_group carrier_delay weather_delay nas_delay security_delay late_aircraft_delay div_reached_dest planned_departure_utc time_at_prediction_utc origin_station_id dest_station_id origin_wnd_angle origin_wnd_angle_qc origin_wnd_type origin_wnd_speed origin_wnd_speed_qc origin_cig_cloud_agl origin_cig_cloud_agl_qc origin_cig_method origin_cig_cavok origin_vis_dist origin_vis_dist_qc origin_vis_var origin_vis_var_qc origin_tmp_c origin_tmp_qc origin_dew_c origin_dew_qc origin_slp_p origin_slp_qc origin_weather_offset_minutes pct_delayed_from_origin mean_delay_from_origin pct_delayed_to_dest mean_delay_to_dest pct_delayed_for_route mean_delay_for_route pct_delayed_from_state mean_delay_from_state pct_delayed_to_state mean_delay_to_state index_id origin_wnd_type_null origin_wnd_speed_null origin_cig_cloud_agl_null origin_cig_cavok_null origin_vis_dist_null origin_vis_var_null origin_tmp_c_null origin_dew_c_null origin_slp_p_null holiday KMCO -5 America/New_York 28.429399490356445 -81.30899810791016 96.0 KPVD -5 America/New_York 41.732601 -71.420403 55.0 2017 4 10 29 7 2017-10-29 F9 N713FR 1734 FL Orlando, FL 13204 MCO RI Providence, RI 14307 PVD 1915 1925 0.0 null null 1900-1959 null null null 2200-2259 false null true 170.0 null 1.0 1072.0 5 null null null null null false 2017-10-29T23:15:00.000+0000 2017-10-29T21:15:00.000+0000 72205012815 72507014765 280 5 N 82.0 5 22000.0 5 9 N 16093.0 5 N 5 183.0 5 22.0 5 10079.0 5 -22.0 21.710211902785975 12.192814185929373 22.234881102205737 10.609204233841588 25.74221247830456 14.528132992327366 20.73620691585407 11.050036683785766 22.234881102205737 10.609204233841588 16160474 false false false false false false false false false non-holiday KBTV -5 America/New_York 44.471900939899996 -73.15329742429999 335.0 KDTW -5 America/New_York 42.212398529052734 -83.35340118408203 645.0 2018 1 1 1 1 2018-01-01 9E N834AY 3427 VT Burlington, VT 10785 BTV MI Detroit, MI 11433 DTW 0529 529 0.0 null null 0001-0559 730 -20.0 -2 0700-0759 false null false 141.0 121.0 1.0 537.0 3 null null null null null null 2018-01-01T10:29:00.000+0000 2018-01-01T08:29:00.000+0000 72617014742 72537094847 360 5 N 31.0 5 22000.0 5 9 N 16093.0 5 N 5 -217.0 5 -267.0 5 10281.0 5 -35.0 21.655987184621544 12.591669443518827 16.165105905505516 8.95060912363481 15.54591467823572 10.66294964028777 21.655987184621544 12.591669443518827 16.81402361118209 9.12416861223111 17111208 false false false false false false false false false holiday KCVG -5 America/New_York 39.0488014221 -84.6678009033 896.0 KMSP -6 America/Chicago 44.882 -93.221802 841.0 2018 1 1 1 1 2018-01-01 9E N936XJ 3407 KY Cincinnati, OH 11193 CVG MN Minneapolis, MN 13487 MSP 0700 700 0.0 null null 0700-0759 816 1.0 0 0800-0859 false null false 135.0 136.0 1.0 596.0 3 null null null null null null 2018-01-01T12:00:00.000+0000 2018-01-01T10:00:00.000+0000 72421093814 72658014922 320 5 N 31.0 5 427.0 5 M N 16093.0 5 N 5 -167.0 5 -189.0 5 10368.0 5 -8.0 18.383595476407123 9.930785405552744 15.40571797423415 8.17815405516324 14.668218859138532 7.971224410969486 18.113217237546362 9.71168133354347 15.51499295740704 8.257378442592778 17112859 false false false false false false false false false holiday KDFW -6 America/Chicago 32.896801 -97.038002 607.0 KJFK -5 America/New_York 40.63980103 -73.77890015 13.0 2018 1 1 1 1 2018-01-01 9E N905XJ 3789 TX Dallas/Fort Worth, TX 

There are only 4744 nulls out of over 32M. These appear to be data entry issues. Since it is such a small subset, we will opt to drop these rows and write out our final model data.

In [0]:
model_data.dropna(how='any').write.mode('overwrite').parquet(f"{blob_url}/model_features_v6")